# Download the datasets and save it in google drive.

In [52]:
import kagglehub
import os
import shutil

if False:
  # Download latest version of the dataset
  download_temp_path = kagglehub.dataset_download("sloozecareers/slooze-challenge")

  # User-specified destination path
  destination_path = "/content/drive/MyDrive/Colab Notebooks/Slooze/datasets"

  # Create the destination directory if it does not exist
  os.makedirs(destination_path, exist_ok=True)

  # Copy the contents of the downloaded directory to the destination path
  for item in os.listdir(download_temp_path):
      source_item_path = os.path.join(download_temp_path, item)
      destination_item_path = os.path.join(destination_path, item)

      if os.path.isdir(source_item_path):
          # Use copytree for directories. dirs_exist_ok=True allows merging if directory already exists.
          shutil.copytree(source_item_path, destination_item_path, dirs_exist_ok=True)
      else:
          # Use copy2 for files to preserve metadata
          shutil.copy2(source_item_path, destination_item_path)

  print(f"Dataset successfully downloaded and copied to: {destination_path}")

# ***START***

# Import Libraries

In [53]:
# Data manipulation
import pandas as pd
import numpy as np
import warnings
warnings.filterwarnings('ignore')

# Visualization
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Date handling
from datetime import datetime, timedelta

# Statistical analysis
from scipy import stats

# Machine Learning & Forecasting
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error, mean_squared_error
from prophet import Prophet

# Kaggle dataset download
import kagglehub

# File system
import os

# Display settings
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 100)
plt.style.use('seaborn-v0_8-darkgrid')

print("All libraries imported successfully!")

All libraries imported successfully!


# Download Dataset from Kaggle

In [54]:
import kagglehub

print("Downloading Slooze Challenge dataset from Kaggle...\n")

# Download latest version
path = kagglehub.dataset_download("sloozecareers/slooze-challenge")

print("\n" + "="*60)
print("Dataset downloaded successfully!")
print("="*60)
print(f"Path to dataset files: {path}")


Using Colab cache for faster access to the 'slooze-challenge' dataset.

Dataset downloaded successfully!
Path to dataset files: /kaggle/input/slooze-challenge


# List All Files in Dataset

In [55]:

actual_path = os.path.join(path, 'slooze_challenge')

print("Checking actual file structure...\n")
print(f"Main path: {path}")
print(f"Subfolder path: {actual_path}\n")

# List files in the subfolder
print("Files in slooze_challenge folder:\n")

files = os.listdir(actual_path)
for file in sorted(files):
    file_path = os.path.join(actual_path, file)
    size_mb = os.path.getsize(file_path) / (1024 * 1024)
    print(f"   {file:<35} ({size_mb:>7.2f} MB)")

print("\n" + "="*60)

Checking actual file structure...

Main path: /kaggle/input/slooze-challenge
Subfolder path: /kaggle/input/slooze-challenge/slooze_challenge

Files in slooze_challenge folder:

   2017PurchasePricesDec.csv           (   1.10 MB)
   BegInvFINAL12312016.csv             (  18.41 MB)
   EndInvFINAL12312016.csv             (  20.03 MB)
   InvoicePurchases12312016.csv        (   0.56 MB)
   PurchasesFINAL12312016.csv          ( 383.14 MB)
   SalesFINAL12312016.csv              ( 121.94 MB)



# Define File Paths

In [56]:
# Files are in the slooze_challenge subfolder
file_paths = {
    'purchase_prices': os.path.join(actual_path, '2017PurchasePricesDec.csv'),
    'beg_inventory': os.path.join(actual_path, 'BegInvFINAL12312016.csv'),
    'end_inventory': os.path.join(actual_path, 'EndInvFINAL12312016.csv'),
    'invoice_purchases': os.path.join(actual_path, 'InvoicePurchases12312016.csv'),
    'purchases': os.path.join(actual_path, 'PurchasesFINAL12312016.csv'),
    'sales': os.path.join(actual_path, 'SalesFINAL12312016.csv')
}

print("File paths configured correctly!")
print("\nFiles to load:")
for key, file_path in file_paths.items():
    exists = "" if os.path.exists(file_path) else "Not"
    print(f"  {exists} {key:<20}: {os.path.basename(file_path)}")

File paths configured correctly!

Files to load:
   purchase_prices     : 2017PurchasePricesDec.csv
   beg_inventory       : BegInvFINAL12312016.csv
   end_inventory       : EndInvFINAL12312016.csv
   invoice_purchases   : InvoicePurchases12312016.csv
   purchases           : PurchasesFINAL12312016.csv
   sales               : SalesFINAL12312016.csv


# Load All CSV Files

In [57]:
print("\nLoading datasets... This may take 2-3 minutes for large files.\n")
print("="*60)

# Dictionary to store all dataframes
data = {}

# Load each file with progress updates
for key, file_path in file_paths.items():
    print(f"Loading {key}...", end=" ")
    try:
        data[key] = pd.read_csv(file_path, low_memory=False)
        rows, cols = data[key].shape
        print(f"Loaded! {rows:,} rows × {cols} columns")
    except Exception as e:
        print(f"Error: {e}")

print("="*60)

# Check if all files loaded successfully
if len(data) == 6:
    print("ALL FILES LOADED SUCCESSFULLY!")
else:
    print(f"WARNING: Only {len(data)}/6 files loaded!")

print("="*60)


Loading datasets... This may take 2-3 minutes for large files.

Loading purchase_prices... Loaded! 12,261 rows × 9 columns
Loading beg_inventory... Loaded! 206,529 rows × 9 columns
Loading end_inventory... Loaded! 224,489 rows × 9 columns
Loading invoice_purchases... Loaded! 5,543 rows × 10 columns
Loading purchases... Loaded! 2,372,474 rows × 16 columns
Loading sales... Loaded! 1,048,575 rows × 14 columns
ALL FILES LOADED SUCCESSFULLY!


# Quick Overview of Each Dataset

In [58]:
print("\nDATASET OVERVIEW\n")

for key, df in data.items():
    print("="*60)
    print(f"{key.upper().replace('_', ' ')}")
    print("="*60)
    print(f"Shape: {df.shape[0]:,} rows × {df.shape[1]} columns")
    print(f"Memory: {df.memory_usage(deep=True).sum() / 1024**2:.2f} MB")
    print(f"\nColumns ({len(df.columns)}):")
    print(f"{list(df.columns)}")
    print(f"\nFirst 3 rows:")
    display(df.head(3))
    print("\n")


DATASET OVERVIEW

PURCHASE PRICES
Shape: 12,261 rows × 9 columns
Memory: 3.43 MB

Columns (9):
['Brand', 'Description', 'Price', 'Size', 'Volume', 'Classification', 'PurchasePrice', 'VendorNumber', 'VendorName']

First 3 rows:


Brand                  Description  Price   Size Volume  Classification  \
0     58  Gekkeikan Black & Gold Sake  12.99  750mL    750               1   
1     62     Herradura Silver Tequila  36.99  750mL    750               1   
2     63   Herradura Reposado Tequila  38.99  750mL    750               1   

   PurchasePrice  VendorNumber                   VendorName  
0           9.28          8320  SHAW ROSS INT L IMP LTD      
1          28.67          1128  BROWN-FORMAN CORP            
2          30.46          1128  BROWN-FORMAN CORP



BEG INVENTORY
Shape: 206,529 rows × 9 columns
Memory: 66.94 MB

Columns (9):
['InventoryId', 'Store', 'City', 'Brand', 'Description', 'Size', 'onHand', 'Price', 'startDate']

First 3 rows:


InventoryId  Store          City  Brand                  Description  \
0  1_HARDERSFIELD_58      1  HARDERSFIELD     58  Gekkeikan Black & Gold Sake   
1  1_HARDERSFIELD_60      1  HARDERSFIELD     60       Canadian Club 1858 VAP   
2  1_HARDERSFIELD_62      1  HARDERSFIELD     62     Herradura Silver Tequila   

    Size  onHand  Price   startDate  
0  750mL       8  12.99  2016-01-01  
1  750mL       7  10.99  2016-01-01  
2  750mL       6  36.99  2016-01-01



END INVENTORY
Shape: 224,489 rows × 9 columns
Memory: 72.74 MB

Columns (9):
['InventoryId', 'Store', 'City', 'Brand', 'Description', 'Size', 'onHand', 'Price', 'endDate']

First 3 rows:


...

VendorNumber                   VendorName InvoiceDate  PONumber  \
0           105  ALTAMAR BRANDS LLC           2016-01-04      8124   
1          4466  AMERICAN VINTAGE BEVERAGE    2016-01-07      8137   
2           388  ATLANTIC IMPORTING COMPANY   2016-01-09      8169   

       PODate     PayDate  Quantity  Dollars  Freight Approval  
0  2015-12-21  2016-02-16         6   214.26     3.47      NaN  
1  2015-12-22  2016-02-21        15   140.55     8.57      NaN  
2  2015-12-24  2016-02-16         5   106.60     4.61      NaN



PURCHASES
Shape: 2,372,474 rows × 16 columns
Memory: 1278.97 MB

Columns (16):
['InventoryId', 'Store', 'Brand', 'Description', 'Size', 'VendorNumber', 'VendorName', 'PONumber', 'PODate', 'ReceivingDate', 'InvoiceDate', 'PayDate', 'PurchasePrice', 'Quantity', 'Dollars', 'Classification']

First 3 rows:


InventoryId  Store  Brand                   Description   Size  \
0  69_MOUNTMEND_8412     69   8412     Tequila Ocho Plata Fresno  750mL   
1   30_CULCHETH_5255     30   5255  TGI Fridays Ultimte Mudslide  1.75L   
2  34_PITMERDEN_5215     34   5215  TGI Fridays Long Island Iced  1.75L   

   VendorNumber                   VendorName  PONumber      PODate  \
0           105  ALTAMAR BRANDS LLC               8124  2015-12-21   
1          4466  AMERICAN VINTAGE BEVERAGE        8137  2015-12-22   
2          4466  AMERICAN VINTAGE BEVERAGE        8137  2015-12-22   

  ReceivingDate InvoiceDate     PayDate  PurchasePrice  Quantity  Dollars  \
0    2016-01-02  2016-01-04  2016-02-16          35.71         6   214.26   
1    2016-01-01  2016-01-07  2016-02-21           9.35         4    37.40   
2    2016-01-02  2016-01-07  2016-02-21           9.41         5    47.05   

   Classification  
0               1  
1               1  
2               1



SALES
Shape: 1,048,575 rows × 14 columns
Memory: 395.01 MB

Columns (14):
['InventoryId', 'Store', 'Brand', 'Description', 'Size', 'SalesQuantity', 'SalesDollars', 'SalesPrice', 'SalesDate', 'Volume', 'Classification', 'ExciseTax', 'VendorNo', 'VendorName']

First 3 rows:


InventoryId  Store  Brand                 Description   Size  \
0  1_HARDERSFIELD_1004      1   1004  Jim Beam w/2 Rocks Glasses  750mL   
1  1_HARDERSFIELD_1004      1   1004  Jim Beam w/2 Rocks Glasses  750mL   
2  1_HARDERSFIELD_1004      1   1004  Jim Beam w/2 Rocks Glasses  750mL   

   SalesQuantity  SalesDollars  SalesPrice SalesDate  Volume  Classification  \
0              1         16.49       16.49  1/1/2016     750               1   
1              2         32.98       16.49  1/2/2016     750               1   
2              1         16.49       16.49  1/3/2016     750               1   

   ExciseTax  VendorNo                   VendorName  
0       0.79     12546  JIM BEAM BRANDS COMPANY      
1       1.57     12546  JIM BEAM BRANDS COMPANY      
2       0.79     12546  JIM BEAM BRANDS COMPANY

# Detailed Data Profiling

In [59]:
def profile_dataset(df, name):
    """
    Generate a detailed profile report for a dataset
    """
    print("="*70)
    print(f"DETAILED PROFILE: {name.upper()}")
    print("="*70)

    # Basic info
    print(f"\n1️ BASIC INFO:")
    print(f"   Rows: {df.shape[0]:,}")
    print(f"   Columns: {df.shape[1]}")
    print(f"   Memory: {df.memory_usage(deep=True).sum() / 1024**2:.2f} MB")

    # Data types
    print(f"\n2️ DATA TYPES:")
    print(df.dtypes.value_counts())

    # Missing values
    print(f"\n3️ MISSING VALUES:")
    missing = df.isnull().sum()
    missing_pct = (missing / len(df)) * 100
    missing_df = pd.DataFrame({
        'Missing Count': missing[missing > 0],
        'Percentage': missing_pct[missing > 0]
    }).sort_values('Percentage', ascending=False)

    if len(missing_df) > 0:
        print(missing_df)
    else:
        print("    No missing values!")

    # Duplicates
    print(f"\n4️ DUPLICATES:")
    duplicates = df.duplicated().sum()
    print(f"   Duplicate rows: {duplicates:,} ({(duplicates/len(df)*100):.2f}%)")

    # Numeric columns summary
    print(f"\n5️ NUMERIC COLUMNS SUMMARY:")
    numeric_cols = df.select_dtypes(include=[np.number]).columns
    if len(numeric_cols) > 0:
        print(df[numeric_cols].describe().T)
    else:
        print("   No numeric columns found")

    print("\n" + "="*70 + "\n")

# Profile each dataset
for key, df in data.items():
    profile_dataset(df, key)

DETAILED PROFILE: PURCHASE_PRICES

1️ BASIC INFO:
   Rows: 12,261
   Columns: 9
   Memory: 3.43 MB

2️ DATA TYPES:
object     4
int64      3
float64    2
Name: count, dtype: int64

3️ MISSING VALUES:
             Missing Count  Percentage
Description              1    0.008156
Size                     1    0.008156
Volume                   1    0.008156

4️ DUPLICATES:
   Duplicate rows: 0 (0.00%)

5️ NUMERIC COLUMNS SUMMARY:
                  count          mean           std   min      25%       50%  \
Brand           12261.0  17989.067123  12528.503464  58.0  5990.00  18788.00   
Price           12261.0     38.640240    206.151172   0.0    10.99     15.99   
Classification  12261.0      1.708996      0.454244   1.0     1.00      2.00   
PurchasePrice   12261.0     26.488220    156.182948   0.0     6.89     10.65   
VendorNumber    12261.0  10814.861757  19007.682322   2.0  3960.00   7153.00   

                     75%        max  
Brand           25117.00   90631.00  
Price        

# Data Cleaning Function

In [60]:
def clean_dataset(df, name):
    """
    Clean a dataset by handling missing values and duplicates
    """
    print(f"Cleaning {name}...")

    original_shape = df.shape

    # 1. Remove completely empty rows
    df = df.dropna(how='all')

    # 2. Remove duplicate rows
    df = df.drop_duplicates()

    # 3. Handle date columns (convert to datetime)
    date_columns = [col for col in df.columns if 'date' in col.lower() or 'time' in col.lower()]
    for col in date_columns:
        try:
            df[col] = pd.to_datetime(df[col], errors='coerce')
            print(f"    Converted {col} to datetime")
        except:
            pass

    # 4. Strip whitespace from string columns
    string_cols = df.select_dtypes(include=['object']).columns
    for col in string_cols:
        if df[col].dtype == 'object':
            df[col] = df[col].str.strip()

    print(f"   Original: {original_shape[0]:,} rows")
    print(f"   After cleaning: {df.shape[0]:,} rows")
    print(f"   Removed: {original_shape[0] - df.shape[0]:,} rows")
    print(f"   Cleaning complete!\n")

    return df

# Clean all datasets
print(" CLEANING ALL DATASETS\n")
print("="*60)

cleaned_data = {}
for key, df in data.items():
    cleaned_data[key] = clean_dataset(df.copy(), key)

print("="*60)
print(" ALL DATASETS CLEANED!")

 CLEANING ALL DATASETS

Cleaning purchase_prices...
   Original: 12,261 rows
   After cleaning: 12,261 rows
   Removed: 0 rows
   Cleaning complete!

Cleaning beg_inventory...
    Converted startDate to datetime
   Original: 206,529 rows
   After cleaning: 206,529 rows
   Removed: 0 rows
   Cleaning complete!

Cleaning end_inventory...
    Converted endDate to datetime
   Original: 224,489 rows
   After cleaning: 224,489 rows
   Removed: 0 rows
   Cleaning complete!

Cleaning invoice_purchases...
    Converted InvoiceDate to datetime
    Converted PODate to datetime
    Converted PayDate to datetime
   Original: 5,543 rows
   After cleaning: 5,543 rows
   Removed: 0 rows
   Cleaning complete!

Cleaning purchases...
    Converted PODate to datetime
    Converted ReceivingDate to datetime
    Converted InvoiceDate to datetime
    Converted PayDate to datetime
   Original: 2,372,474 rows
   After cleaning: 2,372,474 rows
   Removed: 0 rows
   Cleaning complete!

Cleaning sales...
    Conv

# Summary Statistics

In [61]:
print("\nCLEANED DATA SUMMARY\n")
print("="*70)

summary_data = []
for key, df in cleaned_data.items():
    summary_data.append({
        'Dataset': key.replace('_', ' ').title(),
        'Rows': f"{df.shape[0]:,}",
        'Columns': df.shape[1],
        'Memory (MB)': f"{df.memory_usage(deep=True).sum() / 1024**2:.2f}"
    })

summary_df = pd.DataFrame(summary_data)
display(summary_df)

print("="*70)


CLEANED DATA SUMMARY



Dataset       Rows  Columns Memory (MB)
0    Purchase Prices     12,261        9        3.36
1      Beg Inventory    206,529        9       56.89
2      End Inventory    224,489        9       61.82
3  Invoice Purchases      5,543       10        0.88
4          Purchases  2,372,474       16      803.19
5              Sales  1,048,575       14      339.07

# Calculate Product-Level Revenue
Aggregating total sales revenue for each product across all stores and dates.

In [62]:
print("ABC ANALYSIS - Calculate Product Revenue\n")
print("="*70)

# Use sales data
sales_df = cleaned_data['sales'].copy()

# Group by product (Brand + Description) and calculate total revenue
product_revenue = sales_df.groupby(['Brand', 'Description']).agg({
    'SalesDollars': 'sum',
    'SalesQuantity': 'sum',
    'InventoryId': 'count'  # Number of transactions
}).reset_index()

# Rename columns for clarity
product_revenue.columns = ['Brand', 'Description', 'TotalRevenue', 'TotalQuantitySold', 'TransactionCount']

# Sort by revenue (descending)
product_revenue = product_revenue.sort_values('TotalRevenue', ascending=False).reset_index(drop=True)

print(f"Total Unique Products: {len(product_revenue):,}")
print(f"Total Revenue: ${product_revenue['TotalRevenue'].sum():,.2f}")
print(f"Total Units Sold: {product_revenue['TotalQuantitySold'].sum():,.0f}")

print("\nTop 10 Products by Revenue:\n")
display(product_revenue.head(10))

print("="*70)

ABC ANALYSIS - Calculate Product Revenue

Total Unique Products: 7,658
Total Revenue: $33,139,375.29
Total Units Sold: 2,451,169

Top 10 Products by Revenue:



Brand                Description  TotalRevenue  TotalQuantitySold  \
0   4261     Capt Morgan Spiced Rum     444810.74              20226   
1   3545            Ketel One Vodka     357759.17              11883   
2   1233    Jack Daniels No 7 Black     344712.22               9578   
3   8068           Absolut 80 Proof     288135.11              11189   
4   3405      Tito's Handmade Vodka     275162.97               9203   
5   3858           Grey Goose Vodka     225014.22               9378   
6   2589      Jameson Irish Whiskey     191669.51               4649   
7   4227  Bacardi Superior Rum Trav     183659.91              10209   
8   1376                   Jim Beam     169922.38               7362   
9   2585      Jameson Irish Whiskey     164426.60               6940   

   TransactionCount  
0              1969  
1              1749  
2              1803  
3              1870  
4              1750  
5              1762  
6              1407  
7              1699  
8              1841  
9              1735

# Calculate Cumulative Revenue Percentage
Computing what percentage of total revenue each product contributes cumulatively.

In [63]:
print("\nABC ANALYSIS - Calculate Cumulative Metrics\n")
print("="*70)

# Calculate percentage of total revenue
product_revenue['RevenuePercentage'] = (product_revenue['TotalRevenue'] / product_revenue['TotalRevenue'].sum()) * 100

# Calculate cumulative revenue percentage
product_revenue['CumulativeRevenuePercentage'] = product_revenue['RevenuePercentage'].cumsum()

# Calculate cumulative product count percentage
product_revenue['CumulativeProductPercentage'] = ((product_revenue.index + 1) / len(product_revenue)) * 100

print(" Cumulative metrics calculated!")

print("\n Sample with Cumulative Percentages:\n")
display(product_revenue[['Brand', 'Description', 'TotalRevenue', 'RevenuePercentage',
                         'CumulativeRevenuePercentage', 'CumulativeProductPercentage']].head(15))

print("="*70)


ABC ANALYSIS - Calculate Cumulative Metrics

 Cumulative metrics calculated!

 Sample with Cumulative Percentages:



Brand                Description  TotalRevenue  RevenuePercentage  \
0    4261     Capt Morgan Spiced Rum     444810.74           1.342242   
1    3545            Ketel One Vodka     357759.17           1.079559   
2    1233    Jack Daniels No 7 Black     344712.22           1.040189   
3    8068           Absolut 80 Proof     288135.11           0.869465   
4    3405      Tito's Handmade Vodka     275162.97           0.830320   
5    3858           Grey Goose Vodka     225014.22           0.678994   
6    2589      Jameson Irish Whiskey     191669.51           0.578374   
7    4227  Bacardi Superior Rum Trav     183659.91           0.554205   
8    1376                   Jim Beam     169922.38           0.512751   
9    2585      Jameson Irish Whiskey     164426.60           0.496167   
10   8680                Crown Royal     162059.53           0.489024   
11   2757   Johnnie Walker Red Label     155678.09           0.469768   
12   5364                     Kahlua     149137.09           0.450030   
13   3876          Smirnoff 80 Proof     144969.26           0.437453   
14   3802         Three Olives Vodka     142887.85           0.431172   

    CumulativeRevenuePercentage  CumulativeProductPercentage  
0                      1.342242                     0.013058  
1                      2.421802                     0.026116  
2                      3.461991                     0.039175  
3                      4.331455                     0.052233  
4                      5.161776                     0.065291  
5                      5.840769                     0.078349  
6                      6.419143                     0.091408  
7                      6.973348                     0.104466  
8                      7.486098                     0.117524  
9                      7.982265                     0.130582  
10                     8.471289                     0.143641  
11                     8.941057                     0.156699  
12                     9.391087                     0.169757  
13                     9.828540                     0.182815  
14                    10.259713                     0.195874

# Assign ABC Classification
Categorizing each product into A, B, or C class based on cumulative revenue contribution.

In [64]:
print("\n ABC ANALYSIS - Assign ABC Categories\n")
print("="*70)

def assign_abc_category(cumulative_revenue_pct):
    """
    Assign ABC category based on cumulative revenue percentage
    A: Top products contributing to first 80% of revenue
    B: Products contributing to next 15% of revenue (80-95%)
    C: Products contributing to last 5% of revenue (95-100%)
    """
    if cumulative_revenue_pct <= 80:
        return 'A'
    elif cumulative_revenue_pct <= 95:
        return 'B'
    else:
        return 'C'

# Apply ABC classification
product_revenue['ABC_Category'] = product_revenue['CumulativeRevenuePercentage'].apply(assign_abc_category)

print("ABC Categories assigned!")

# Summary statistics by category
abc_summary = product_revenue.groupby('ABC_Category').agg({
    'Brand': 'count',  # Number of products
    'TotalRevenue': 'sum',
    'TotalQuantitySold': 'sum'
}).reset_index()

abc_summary.columns = ['ABC_Category', 'ProductCount', 'TotalRevenue', 'TotalUnitsSold']
abc_summary['RevenuePercentage'] = (abc_summary['TotalRevenue'] / abc_summary['TotalRevenue'].sum()) * 100
abc_summary['ProductPercentage'] = (abc_summary['ProductCount'] / abc_summary['ProductCount'].sum()) * 100

print("\nABC CATEGORY SUMMARY:\n")
display(abc_summary)

print("\n" + "="*70)


 ABC ANALYSIS - Assign ABC Categories

ABC Categories assigned!

ABC CATEGORY SUMMARY:



ABC_Category  ProductCount  TotalRevenue  TotalUnitsSold  RevenuePercentage  \
0            A          1502   26509374.02         1871415          79.993584   
1            B          1813    4971817.15          450870          15.002749   
2            C          4343    1658184.12          128884           5.003667   

   ProductPercentage  
0          19.613476  
1          23.674589  
2          56.711935

# Visualize ABC Analysis - Pareto Chart
Creating a Pareto chart to visualize the 80/20 rule in action.

In [65]:
print("\n ABC ANALYSIS - Create Pareto Chart\n")
print("="*70)

# Create Pareto Chart
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Bar chart - Product count
fig.add_trace(
    go.Bar(
        x=product_revenue.index[:100],  # First 100 products
        y=product_revenue['TotalRevenue'][:100],
        name='Revenue per Product',
        marker_color='steelblue'
    ),
    secondary_y=False
)

# Line chart - Cumulative percentage
fig.add_trace(
    go.Scatter(
        x=product_revenue.index[:100],
        y=product_revenue['CumulativeRevenuePercentage'][:100],
        name='Cumulative Revenue %',
        line=dict(color='red', width=3),
        mode='lines'
    ),
    secondary_y=True
)

# Add reference lines for ABC boundaries
fig.add_hline(y=80, line_dash="dash", line_color="green",
              annotation_text="A-B Boundary (80%)", secondary_y=True)
fig.add_hline(y=95, line_dash="dash", line_color="orange",
              annotation_text="B-C Boundary (95%)", secondary_y=True)

# Update layout
fig.update_layout(
    title='ABC Analysis - Pareto Chart (Top 100 Products)',
    xaxis_title='Product Rank',
    height=600,
    hovermode='x unified',
    showlegend=True
)

fig.update_yaxes(title_text="Revenue ($)", secondary_y=False)
fig.update_yaxes(title_text="Cumulative Revenue (%)", secondary_y=True, range=[0, 105])

fig.show()

print("Pareto chart generated!")
print("="*70)


 ABC ANALYSIS - Create Pareto Chart



Pareto chart generated!


# Visualize ABC Category Distribution
Creating pie charts and bar charts to show the distribution of products and revenue across ABC categories.

In [66]:
print("\n ABC ANALYSIS - Category Distribution Charts\n")
print("="*70)

# Create subplots: 2 pie charts side by side
fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=('Product Count by ABC Category', 'Revenue Distribution by ABC Category'),
    specs=[[{'type':'pie'}, {'type':'pie'}]]
)

# Pie chart 1: Product count
fig.add_trace(
    go.Pie(
        labels=abc_summary['ABC_Category'],
        values=abc_summary['ProductCount'],
        marker=dict(colors=['#2ecc71', '#f39c12', '#e74c3c']),
        textinfo='label+percent',
        name='Products'
    ),
    row=1, col=1
)

# Pie chart 2: Revenue
fig.add_trace(
    go.Pie(
        labels=abc_summary['ABC_Category'],
        values=abc_summary['TotalRevenue'],
        marker=dict(colors=['#2ecc71', '#f39c12', '#e74c3c']),
        textinfo='label+percent',
        name='Revenue'
    ),
    row=1, col=2
)

fig.update_layout(height=500, title_text="ABC Category Distribution")
fig.show()

print("Distribution charts generated!")
print("="*70)


 ABC ANALYSIS - Category Distribution Charts



Distribution charts generated!


# Detailed Breakdown by Category
Showing sample products from each ABC category with their metrics.

In [67]:
print("\nABC ANALYSIS - Detailed Category Breakdown\n")
print("="*70)

for category in ['A', 'B', 'C']:
    category_data = product_revenue[product_revenue['ABC_Category'] == category]

    print(f"\n{'='*70}")
    print(f"  CATEGORY {category}")
    print(f"{'='*70}")
    print(f"Total Products: {len(category_data):,}")
    print(f"Total Revenue: ${category_data['TotalRevenue'].sum():,.2f}")
    print(f"Average Revenue per Product: ${category_data['TotalRevenue'].mean():,.2f}")
    print(f"Revenue Range: ${category_data['TotalRevenue'].min():,.2f} - ${category_data['TotalRevenue'].max():,.2f}")

    print(f"\n Top 5 Products in Category {category}:\n")
    display(category_data[['Brand', 'Description', 'TotalRevenue', 'TotalQuantitySold',
                           'RevenuePercentage', 'CumulativeRevenuePercentage']].head(5))

print("\n" + "="*70)


ABC ANALYSIS - Detailed Category Breakdown


  CATEGORY A
Total Products: 1,502
Total Revenue: $26,509,374.02
Average Revenue per Product: $17,649.38
Revenue Range: $5,037.90 - $444,810.74

 Top 5 Products in Category A:



Brand              Description  TotalRevenue  TotalQuantitySold  \
0   4261   Capt Morgan Spiced Rum     444810.74              20226   
1   3545          Ketel One Vodka     357759.17              11883   
2   1233  Jack Daniels No 7 Black     344712.22               9578   
3   8068         Absolut 80 Proof     288135.11              11189   
4   3405    Tito's Handmade Vodka     275162.97               9203   

   RevenuePercentage  CumulativeRevenuePercentage  
0           1.342242                     1.342242  
1           1.079559                     2.421802  
2           1.040189                     3.461991  
3           0.869465                     4.331455  
4           0.830320                     5.161776


  CATEGORY B
Total Products: 1,813
Total Revenue: $4,971,817.15
Average Revenue per Product: $2,742.32
Revenue Range: $1,341.86 - $5,035.03

 Top 5 Products in Category B:



Brand                   Description  TotalRevenue  TotalQuantitySold  \
1502  24286  Kendall Jackson Gr RSV Cab S       5035.03                197   
1503    759     Bunnahabhain 12 Yr Single       5027.04                 96   
1504   5334               Kahlua Especial       5026.95                205   
1505    757                  Jim Beam Rye       5026.22                278   
1506  32796     Warre's Otima 10-Yr Tawny       5023.49                251   

      RevenuePercentage  CumulativeRevenuePercentage  
1502           0.015193                    80.008778  
1503           0.015169                    80.023947  
1504           0.015169                    80.039116  
1505           0.015167                    80.054283  
1506           0.015159                    80.069442


  CATEGORY C
Total Products: 4,343
Total Revenue: $1,658,184.12
Average Revenue per Product: $381.81
Revenue Range: $0.98 - $1,339.93

 Top 5 Products in Category C:



Brand                   Description  TotalRevenue  TotalQuantitySold  \
3315  20204           Dibon Cava Brut Rsv       1339.93                107   
3316  20800  Talamonti Moda Montepulciano       1339.51                149   
3317  15334      Brotte La Griveliere CDR       1338.66                134   
3318   1065  DiSaronno Cavalli Collection       1337.97                103   
3319  24498                Cuvaison Chard       1337.50                 50   

      RevenuePercentage  CumulativeRevenuePercentage  
3315           0.004043                    95.000376  
3316           0.004042                    95.004418  
3317           0.004039                    95.008457  
3318           0.004037                    95.012495  
3319           0.004036                    95.016531

# Save ABC Analysis Results
Saving the ABC classification results to a CSV file for future reference.

In [68]:
print("\n ABC ANALYSIS - Save Results\n")
print("="*70)

# Save full ABC analysis
abc_output_path = '/content/ABC_Analysis_Results.csv'
product_revenue.to_csv(abc_output_path, index=False)

print(f"ABC Analysis saved to: {abc_output_path}")

# Also save just the summary
abc_summary_path = '/content/ABC_Summary.csv'
abc_summary.to_csv(abc_summary_path, index=False)

print(f"ABC Summary saved to: {abc_summary_path}")

print("\n Files saved successfully!")
print("="*70)


 ABC ANALYSIS - Save Results

ABC Analysis saved to: /content/ABC_Analysis_Results.csv
ABC Summary saved to: /content/ABC_Summary.csv

 Files saved successfully!


# Key Insights & Business Recommendations
Generating actionable business insights from the ABC analysis.

In [69]:
print("\nABC ANALYSIS -Key Insights\n")
print("="*70)

# Calculate key metrics
total_products = len(product_revenue)
a_products = len(product_revenue[product_revenue['ABC_Category'] == 'A'])
b_products = len(product_revenue[product_revenue['ABC_Category'] == 'B'])
c_products = len(product_revenue[product_revenue['ABC_Category'] == 'C'])

a_revenue_pct = abc_summary[abc_summary['ABC_Category'] == 'A']['RevenuePercentage'].values[0]
b_revenue_pct = abc_summary[abc_summary['ABC_Category'] == 'B']['RevenuePercentage'].values[0]
c_revenue_pct = abc_summary[abc_summary['ABC_Category'] == 'C']['RevenuePercentage'].values[0]

print(" KEY INSIGHTS:\n")

print(f"1️ CATEGORY A (High Value Items):")
print(f"   • {a_products:,} products ({(a_products/total_products)*100:.1f}% of inventory)")
print(f"   • Generate ${abc_summary[abc_summary['ABC_Category']=='A']['TotalRevenue'].values[0]:,.2f}")
print(f"   • Contribute {a_revenue_pct:.1f}% of total revenue")
print(f"   •  RECOMMENDATION: Daily monitoring, never stock out, priority reordering\n")

print(f"2️ CATEGORY B (Medium Value Items):")
print(f"   • {b_products:,} products ({(b_products/total_products)*100:.1f}% of inventory)")
print(f"   • Generate ${abc_summary[abc_summary['ABC_Category']=='B']['TotalRevenue'].values[0]:,.2f}")
print(f"   • Contribute {b_revenue_pct:.1f}% of total revenue")
print(f"   •  RECOMMENDATION: Weekly monitoring, maintain safety stock\n")

print(f"3️ CATEGORY C (Low Value Items):")
print(f"   • {c_products:,} products ({(c_products/total_products)*100:.1f}% of inventory)")
print(f"   • Generate ${abc_summary[abc_summary['ABC_Category']=='C']['TotalRevenue'].values[0]:,.2f}")
print(f"   • Contribute {c_revenue_pct:.1f}% of total revenue")
print(f"   •  RECOMMENDATION: Monthly monitoring, consider discontinuing slow movers\n")

print("="*70)
print(" ABC ANALYSIS COMPLETE!")
print("="*70)


ABC ANALYSIS -Key Insights

 KEY INSIGHTS:

1️ CATEGORY A (High Value Items):
   • 1,502 products (19.6% of inventory)
   • Generate $26,509,374.02
   • Contribute 80.0% of total revenue
   •  RECOMMENDATION: Daily monitoring, never stock out, priority reordering

2️ CATEGORY B (Medium Value Items):
   • 1,813 products (23.7% of inventory)
   • Generate $4,971,817.15
   • Contribute 15.0% of total revenue
   •  RECOMMENDATION: Weekly monitoring, maintain safety stock

3️ CATEGORY C (Low Value Items):
   • 4,343 products (56.7% of inventory)
   • Generate $1,658,184.12
   • Contribute 5.0% of total revenue
   •  RECOMMENDATION: Monthly monitoring, consider discontinuing slow movers

 ABC ANALYSIS COMPLETE!


 # DEMAND FORECASTING
 Converting sales data into a time series format with daily aggregations.

In [70]:
print("DEMAND FORECASTING - Prepare Time Series Data\n")
print("="*70)

# Use sales data
sales_df = cleaned_data['sales'].copy()

# Ensure SalesDate is datetime
sales_df['SalesDate'] = pd.to_datetime(sales_df['SalesDate'])

# Aggregate daily sales across all products
daily_sales = sales_df.groupby('SalesDate').agg({
    'SalesDollars': 'sum',
    'SalesQuantity': 'sum'
}).reset_index()

# Sort by date
daily_sales = daily_sales.sort_values('SalesDate').reset_index(drop=True)

# Create additional time features
daily_sales['Year'] = daily_sales['SalesDate'].dt.year
daily_sales['Month'] = daily_sales['SalesDate'].dt.month
daily_sales['DayOfWeek'] = daily_sales['SalesDate'].dt.dayofweek
daily_sales['DayName'] = daily_sales['SalesDate'].dt.day_name()
daily_sales['WeekOfYear'] = daily_sales['SalesDate'].dt.isocalendar().week

print(f" Time series data prepared!")
print(f"   Date Range: {daily_sales['SalesDate'].min()} to {daily_sales['SalesDate'].max()}")
print(f"   Total Days: {len(daily_sales)}")
print(f"   Total Revenue: ${daily_sales['SalesDollars'].sum():,.2f}")

print("\n First 10 days of data:\n")
display(daily_sales.head(10))

print("\n Basic Statistics:\n")
print(daily_sales[['SalesDollars', 'SalesQuantity']].describe())

print("="*70)

DEMAND FORECASTING - Prepare Time Series Data

 Time series data prepared!
   Date Range: 2016-01-01 00:00:00 to 2016-02-29 00:00:00
   Total Days: 60
   Total Revenue: $33,139,375.29

 First 10 days of data:



SalesDate  SalesDollars  SalesQuantity  Year  Month  DayOfWeek    DayName  \
0 2016-01-01     687880.01          49911  2016      1          4     Friday   
1 2016-01-02    1303610.64          93114  2016      1          5   Saturday   
2 2016-01-03     709085.36          53037  2016      1          6     Sunday   
3 2016-01-04     499567.87          41341  2016      1          0     Monday   
4 2016-01-05     496719.05          40831  2016      1          1    Tuesday   
5 2016-01-06     660150.82          51358  2016      1          2  Wednesday   
6 2016-01-07     776881.62          59792  2016      1          3   Thursday   
7 2016-01-08    1336517.75          97389  2016      1          4     Friday   
8 2016-01-09    1428520.90         101690  2016      1          5   Saturday   
9 2016-01-10     611492.80          46146  2016      1          6     Sunday   

   WeekOfYear  
0          53  
1          53  
2          53  
3           1  
4           1  
5           1  
6           1  
7           1  
8           1  
9           1


 Basic Statistics:

       SalesDollars  SalesQuantity
count  6.000000e+01      60.000000
mean   5.523229e+05   40852.816667
std    5.510477e+05   38472.384148
min    6.415285e+04    5425.000000
25%    9.491752e+04    7513.250000
50%    4.981435e+05   41086.000000
75%    7.878177e+05   59825.500000
max    2.721899e+06  180426.000000


# Visualize Overall Sales Trends
Creating visualizations to understand historical sales patterns and seasonality.

In [71]:
print("\n DEMAND FORECASTING - Visualize Sales Trends\n")
print("="*70)

# Create time series plot
fig = make_subplots(
    rows=2, cols=1,
    subplot_titles=('Daily Revenue Trend', 'Daily Units Sold Trend'),
    vertical_spacing=0.15
)

# Revenue trend
fig.add_trace(
    go.Scatter(
        x=daily_sales['SalesDate'],
        y=daily_sales['SalesDollars'],
        mode='lines',
        name='Daily Revenue',
        line=dict(color='steelblue', width=1)
    ),
    row=1, col=1
)

# Add 7-day moving average for revenue
daily_sales['Revenue_MA7'] = daily_sales['SalesDollars'].rolling(window=7).mean()
fig.add_trace(
    go.Scatter(
        x=daily_sales['SalesDate'],
        y=daily_sales['Revenue_MA7'],
        mode='lines',
        name='7-Day Moving Average',
        line=dict(color='red', width=2)
    ),
    row=1, col=1
)

# Quantity trend
fig.add_trace(
    go.Scatter(
        x=daily_sales['SalesDate'],
        y=daily_sales['SalesQuantity'],
        mode='lines',
        name='Daily Units Sold',
        line=dict(color='green', width=1)
    ),
    row=2, col=1
)

# Add 7-day moving average for quantity
daily_sales['Quantity_MA7'] = daily_sales['SalesQuantity'].rolling(window=7).mean()
fig.add_trace(
    go.Scatter(
        x=daily_sales['SalesDate'],
        y=daily_sales['Quantity_MA7'],
        mode='lines',
        name='7-Day Moving Average',
        line=dict(color='orange', width=2)
    ),
    row=2, col=1
)

fig.update_layout(
    height=700,
    title_text=" Sales Trends Over Time (2016)",
    showlegend=True,
    hovermode='x unified'
)

fig.update_xaxes(title_text="Date", row=2, col=1)
fig.update_yaxes(title_text="Revenue ($)", row=1, col=1)
fig.update_yaxes(title_text="Units Sold", row=2, col=1)

fig.show()

print(" Trend visualizations created!")
print("="*70)


 DEMAND FORECASTING - Visualize Sales Trends



 Trend visualizations created!


# Analyze Seasonality Patterns
Examining sales patterns by month, day of week, and week of year to identify seasonality.

In [72]:
print("\n DEMAND FORECASTING - Analyze Seasonality\n")
print("="*70)

# Monthly aggregation
monthly_sales = daily_sales.groupby('Month').agg({
    'SalesDollars': 'mean',
    'SalesQuantity': 'mean'
}).reset_index()

monthly_sales['MonthName'] = monthly_sales['Month'].apply(
    lambda x: datetime(2016, x, 1).strftime('%B')
)

# Day of week aggregation
dow_sales = daily_sales.groupby('DayName').agg({
    'SalesDollars': 'mean',
    'SalesQuantity': 'mean'
}).reindex(['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']).reset_index()

# Create seasonality visualizations
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=('Average Revenue by Month', 'Average Units by Month',
                    'Average Revenue by Day of Week', 'Average Units by Day of Week'),
    specs=[[{'type':'bar'}, {'type':'bar'}],
           [{'type':'bar'}, {'type':'bar'}]]
)

# Monthly revenue
fig.add_trace(
    go.Bar(x=monthly_sales['MonthName'], y=monthly_sales['SalesDollars'],
           marker_color='steelblue', name='Revenue'),
    row=1, col=1
)

# Monthly quantity
fig.add_trace(
    go.Bar(x=monthly_sales['MonthName'], y=monthly_sales['SalesQuantity'],
           marker_color='green', name='Units'),
    row=1, col=2
)

# Day of week revenue
fig.add_trace(
    go.Bar(x=dow_sales['DayName'], y=dow_sales['SalesDollars'],
           marker_color='coral', name='Revenue'),
    row=2, col=1
)

# Day of week quantity
fig.add_trace(
    go.Bar(x=dow_sales['DayName'], y=dow_sales['SalesQuantity'],
           marker_color='orange', name='Units'),
    row=2, col=2
)

fig.update_layout(height=800, title_text=" Seasonality Analysis", showlegend=False)
fig.update_yaxes(title_text="Avg Revenue ($)", row=1, col=1)
fig.update_yaxes(title_text="Avg Units", row=1, col=2)
fig.update_yaxes(title_text="Avg Revenue ($)", row=2, col=1)
fig.update_yaxes(title_text="Avg Units", row=2, col=2)

fig.show()

print(" Seasonality patterns analyzed!")

# Print insights
print("\n SEASONALITY INSIGHTS:\n")
print(" Top 3 Months by Revenue:")
top_months = monthly_sales.nlargest(3, 'SalesDollars')[['MonthName', 'SalesDollars']]
for idx, row in top_months.iterrows():
    print(f"   {row['MonthName']}: ${row['SalesDollars']:,.2f}/day")

print("\n Top 3 Days by Revenue:")
top_days = dow_sales.nlargest(3, 'SalesDollars')[['DayName', 'SalesDollars']]
for idx, row in top_days.iterrows():
    print(f"   {row['DayName']}: ${row['SalesDollars']:,.2f}/day")

print("="*70)


 DEMAND FORECASTING - Analyze Seasonality



 Seasonality patterns analyzed!

 SEASONALITY INSIGHTS:

 Top 3 Months by Revenue:
   January: $963,033.16/day
   February: $113,287.84/day

 Top 3 Days by Revenue:
   Friday: $943,204.24/day
   Saturday: $895,586.45/day
   Sunday: $490,739.96/day


# Prepare Data for Top A-Class Products
Selecting top 5 A-class products for detailed demand forecasting.

In [73]:
print("\n DEMAND FORECASTING - Select Top Products for Forecasting\n")
print("="*70)

# Get top 5 A-class products
top_products = product_revenue[product_revenue['ABC_Category'] == 'A'].head(5)

print("Top 5 Products Selected for Demand Forecasting:\n")
display(top_products[['Brand', 'Description', 'TotalRevenue', 'ABC_Category']])

# Prepare individual product time series
product_forecasts = {}

for idx, product in top_products.iterrows():
    brand = product['Brand']
    description = product['Description']

    # Filter sales for this product
    product_sales = sales_df[
        (sales_df['Brand'] == brand) &
        (sales_df['Description'] == description)
    ].copy()

    # Daily aggregation
    product_daily = product_sales.groupby('SalesDate').agg({
        'SalesQuantity': 'sum',
        'SalesDollars': 'sum'
    }).reset_index()

    # Ensure complete date range (fill missing dates with 0)
    date_range = pd.date_range(
        start=daily_sales['SalesDate'].min(),
        end=daily_sales['SalesDate'].max(),
        freq='D'
    )

    product_daily = product_daily.set_index('SalesDate').reindex(date_range, fill_value=0).reset_index()
    product_daily.columns = ['SalesDate', 'SalesQuantity', 'SalesDollars']

    product_forecasts[f"{brand}_{description}"] = product_daily

    print(f" Prepared data for: {description} (Brand {brand})")

print(f"\n {len(product_forecasts)} products ready for forecasting!")
print("="*70)


 DEMAND FORECASTING - Select Top Products for Forecasting

Top 5 Products Selected for Demand Forecasting:



Brand              Description  TotalRevenue ABC_Category
0   4261   Capt Morgan Spiced Rum     444810.74            A
1   3545          Ketel One Vodka     357759.17            A
2   1233  Jack Daniels No 7 Black     344712.22            A
3   8068         Absolut 80 Proof     288135.11            A
4   3405    Tito's Handmade Vodka     275162.97            A

 Prepared data for: Capt Morgan Spiced Rum (Brand 4261)
 Prepared data for: Ketel One Vodka (Brand 3545)
 Prepared data for: Jack Daniels No 7 Black (Brand 1233)
 Prepared data for: Absolut 80 Proof (Brand 8068)
 Prepared data for: Tito's Handmade Vodka (Brand 3405)

 5 products ready for forecasting!


# Prophet Forecasting Models
Build Prophet Models for Top Products

Using Facebook Prophet to forecast demand for the next 14 days for each top product.

In [74]:
print("\n DEMAND FORECASTING - Build Prophet Models\n")
print("="*70)

# Store forecast results
forecast_results = {}

for product_key, product_data in product_forecasts.items():
    print(f"\n Forecasting for: {product_key}")
    print("-" * 70)

    # Prepare data for Prophet
    prophet_df = product_data[['SalesDate', 'SalesQuantity']].copy()
    prophet_df.columns = ['ds', 'y']

    # Initialize Prophet model with weekly seasonality
    model = Prophet(
        daily_seasonality=True,
        weekly_seasonality=True,
        yearly_seasonality=False,  # Not enough data for yearly
        seasonality_mode='multiplicative',
        changepoint_prior_scale=0.05
    )

    # Fit the model
    print("   Training model...", end=" ")
    model.fit(prophet_df)


    # Create future dataframe for next 14 days
    future = model.make_future_dataframe(periods=14)

    # Make predictions
    print("   Generating forecast...", end=" ")
    forecast = model.predict(future)


    # Store results
    forecast_results[product_key] = {
        'model': model,
        'forecast': forecast,
        'historical': prophet_df
    }

    # Calculate accuracy metrics on historical data
    historical_predictions = forecast[forecast['ds'].isin(prophet_df['ds'])]
    mae = mean_absolute_error(prophet_df['y'], historical_predictions['yhat'])
    rmse = np.sqrt(mean_squared_error(prophet_df['y'], historical_predictions['yhat']))

    print(f"    Model Performance:")
    print(f"      MAE: {mae:.2f} units/day")
    print(f"      RMSE: {rmse:.2f} units/day")

print("\n" + "="*70)
print(f" Forecasting complete for {len(forecast_results)} products!")
print("="*70)


 DEMAND FORECASTING - Build Prophet Models


 Forecasting for: 4261_Capt Morgan Spiced Rum
----------------------------------------------------------------------
   Training model...    Generating forecast...     Model Performance:
      MAE: 135.44 units/day
      RMSE: 185.91 units/day

 Forecasting for: 3545_Ketel One Vodka
----------------------------------------------------------------------
   Training model...    Generating forecast...     Model Performance:
      MAE: 18.97 units/day
      RMSE: 27.90 units/day

 Forecasting for: 1233_Jack Daniels No 7 Black
----------------------------------------------------------------------
   Training model...    Generating forecast...     Model Performance:
      MAE: 62.80 units/day
      RMSE: 85.82 units/day

 Forecasting for: 8068_Absolut 80 Proof
----------------------------------------------------------------------
   Training model...    Generating forecast...     Model Performance:
      MAE: 36.08 units/day
      RMSE: 48.82 uni

# Visualize Forecasts for Each Product
Creating interactive charts showing historical data, forecasts, and confidence intervals for each product.

In [75]:
print("\n DEMAND FORECASTING - Visualize Forecasts\n")
print("="*70)

for product_key, results in forecast_results.items():

    forecast = results['forecast']
    historical = results['historical']

    # Extract product name for title
    product_name = product_key.split('_', 1)[1].replace('_', ' ')

    # Create plot
    fig = go.Figure()

    # Historical data
    fig.add_trace(go.Scatter(
        x=historical['ds'],
        y=historical['y'],
        mode='lines+markers',
        name='Historical Sales',
        line=dict(color='steelblue', width=2),
        marker=dict(size=4)
    ))

    # Forecast
    future_data = forecast[forecast['ds'] > historical['ds'].max()]
    fig.add_trace(go.Scatter(
        x=future_data['ds'],
        y=future_data['yhat'],
        mode='lines+markers',
        name='Forecast',
        line=dict(color='red', width=2, dash='dash'),
        marker=dict(size=6)
    ))

    # Confidence interval
    fig.add_trace(go.Scatter(
        x=future_data['ds'].tolist() + future_data['ds'].tolist()[::-1],
        y=future_data['yhat_upper'].tolist() + future_data['yhat_lower'].tolist()[::-1],
        fill='toself',
        fillcolor='rgba(255, 0, 0, 0.2)',
        line=dict(color='rgba(255,255,255,0)'),
        name='Confidence Interval',
        showlegend=True
    ))

    fig.update_layout(
        title=f' Demand Forecast: {product_name}',
        xaxis_title='Date',
        yaxis_title='Units Sold',
        hovermode='x unified',
        height=500,
        showlegend=True
    )

    fig.show()

    print(f" Visualization created for: {product_name}\n")

print("="*70)


 DEMAND FORECASTING - Visualize Forecasts



 Visualization created for: Capt Morgan Spiced Rum



 Visualization created for: Ketel One Vodka



 Visualization created for: Jack Daniels No 7 Black



 Visualization created for: Absolut 80 Proof



 Visualization created for: Tito's Handmade Vodka



# Create Forecast Summary Table
Generating a summary table with forecasted quantities for the next 14 days for all products.

In [76]:
print("\n DEMAND FORECASTING - Forecast Summary\n")
print("="*70)

# Create summary dataframe
forecast_summary = []

for product_key, results in forecast_results.items():
    forecast = results['forecast']
    product_name = product_key.split('_', 1)[1].replace('_', ' ')

    # Get next 14 days forecast
    future_forecast = forecast[forecast['ds'] > results['historical']['ds'].max()].head(14)

    for _, row in future_forecast.iterrows():
        forecast_summary.append({
            'Product': product_name,
            'Date': row['ds'].strftime('%Y-%m-%d'),
            'Forecasted_Units': max(0, round(row['yhat'])),  # Ensure non-negative
            'Lower_Bound': max(0, round(row['yhat_lower'])),
            'Upper_Bound': max(0, round(row['yhat_upper']))
        })

summary_df = pd.DataFrame(forecast_summary)

print(" 14-DAY FORECAST SUMMARY (First 20 rows):\n")
display(summary_df.head(20))

# Aggregate by product
print("\n TOTAL FORECASTED DEMAND (Next 14 Days):\n")
product_totals = summary_df.groupby('Product').agg({
    'Forecasted_Units': 'sum',
    'Lower_Bound': 'sum',
    'Upper_Bound': 'sum'
}).reset_index()

product_totals.columns = ['Product', 'Total_Forecasted_Units', 'Total_Lower_Bound', 'Total_Upper_Bound']
display(product_totals)

print("="*70)


 DEMAND FORECASTING - Forecast Summary

 14-DAY FORECAST SUMMARY (First 20 rows):



Product        Date  Forecasted_Units  Lower_Bound  \
0   Capt Morgan Spiced Rum  2016-03-01                 7            0   
1   Capt Morgan Spiced Rum  2016-03-02                 2            0   
2   Capt Morgan Spiced Rum  2016-03-03                 0            0   
3   Capt Morgan Spiced Rum  2016-03-04                 0            0   
4   Capt Morgan Spiced Rum  2016-03-05                 0            0   
5   Capt Morgan Spiced Rum  2016-03-06                 0            0   
6   Capt Morgan Spiced Rum  2016-03-07                 0            0   
7   Capt Morgan Spiced Rum  2016-03-08                 0            0   
8   Capt Morgan Spiced Rum  2016-03-09                 0            0   
9   Capt Morgan Spiced Rum  2016-03-10                 0            0   
10  Capt Morgan Spiced Rum  2016-03-11                 0            0   
11  Capt Morgan Spiced Rum  2016-03-12                 0            0   
12  Capt Morgan Spiced Rum  2016-03-13                 0            0   
13  Capt Morgan Spiced Rum  2016-03-14                 0            0   
14         Ketel One Vodka  2016-03-01                19            0   
15         Ketel One Vodka  2016-03-02                21            0   
16         Ketel One Vodka  2016-03-03                29            0   
17         Ketel One Vodka  2016-03-04                64            0   
18         Ketel One Vodka  2016-03-05                70            0   
19         Ketel One Vodka  2016-03-06                45            0   

    Upper_Bound  
0           245  
1           229  
2           241  
3           218  
4           191  
5           190  
6           220  
7           223  
8           202  
9           166  
10          119  
11           37  
12          124  
13          183  
14           56  
15           68  
16          131  
17          399  
18          601  
19          462


 TOTAL FORECASTED DEMAND (Next 14 Days):



Product  Total_Forecasted_Units  Total_Lower_Bound  \
0         Absolut 80 Proof                     607                  8   
1   Capt Morgan Spiced Rum                       9                  0   
2  Jack Daniels No 7 Black                       2                  0   
3          Ketel One Vodka                     570                  0   
4    Tito's Handmade Vodka                     266                  0   

   Total_Upper_Bound  
0               1902  
1               2588  
2               1117  
3               8793  
4               2646

# Save Forecast Results
Saving all forecasts to CSV files for business use.

In [77]:
print("\nDEMAND FORECASTING - Save Forecast Results\n")
print("="*70)

# Save detailed forecast
detailed_forecast_path = '/content/Demand_Forecast_Detailed.csv'
summary_df.to_csv(detailed_forecast_path, index=False)
print(f"Detailed forecast saved to: {detailed_forecast_path}")

# Save product totals
totals_path = '/content/Demand_Forecast_Summary.csv'
product_totals.to_csv(totals_path, index=False)
print(f"Forecast summary saved to: {totals_path}")

print("\nFiles saved successfully!")
print("="*70)


DEMAND FORECASTING - Save Forecast Results

Detailed forecast saved to: /content/Demand_Forecast_Detailed.csv
Forecast summary saved to: /content/Demand_Forecast_Summary.csv

Files saved successfully!


# Business Recommendations from Forecasts
Generating actionable insights based on the forecasts.

In [78]:
print("\n DEMAND FORECASTING - Business Recommendations\n")
print("="*70)

print("\n KEY FORECASTING INSIGHTS:\n")

for idx, row in product_totals.iterrows():
    product = row['Product']
    forecasted = row['Total_Forecasted_Units']
    lower = row['Total_Lower_Bound']
    upper = row['Total_Upper_Bound']

    print(f"{idx+1} {product}:")
    print(f"   Expected demand (14 days): {forecasted:,.0f} units")
    print(f"   Range: {lower:,.0f} - {upper:,.0f} units")
    print(f"    RECOMMENDATION: Order {upper:,.0f} units to avoid stockouts")
    print(f"      (based on upper confidence bound)\n")

print("="*70)
print(" DEMAND FORECASTING COMPLETE!")
print("="*70)


 DEMAND FORECASTING - Business Recommendations


 KEY FORECASTING INSIGHTS:

1 Absolut 80 Proof:
   Expected demand (14 days): 607 units
   Range: 8 - 1,902 units
    RECOMMENDATION: Order 1,902 units to avoid stockouts
      (based on upper confidence bound)

2 Capt Morgan Spiced Rum:
   Expected demand (14 days): 9 units
   Range: 0 - 2,588 units
    RECOMMENDATION: Order 2,588 units to avoid stockouts
      (based on upper confidence bound)

3 Jack Daniels No 7 Black:
   Expected demand (14 days): 2 units
   Range: 0 - 1,117 units
    RECOMMENDATION: Order 1,117 units to avoid stockouts
      (based on upper confidence bound)

4 Ketel One Vodka:
   Expected demand (14 days): 570 units
   Range: 0 - 8,793 units
    RECOMMENDATION: Order 8,793 units to avoid stockouts
      (based on upper confidence bound)

5 Tito's Handmade Vodka:
   Expected demand (14 days): 266 units
   Range: 0 - 2,646 units
    RECOMMENDATION: Order 2,646 units to avoid stockouts
      (based on upper confiden

# Calculate Average Daily Demand (January Data)
Using January data (which is more representative) to calculate realistic daily demand for top products.

In [79]:
print("\n REORDER POINT ANALYSIS - Calculate Daily Demand\n")
print("="*70)

# Use only January data for more reliable averages
sales_df = cleaned_data['sales'].copy()
jan_sales = sales_df[sales_df['SalesDate'].dt.month == 1]

# Calculate daily demand for top 5 products
top_products_list = [
    (4261, 'Capt Morgan Spiced Rum'),
    (3545, 'Ketel One Vodka'),
    (1233, 'Jack Daniels No 7 Black'),
    (8068, 'Absolut 80 Proof'),
    (3405, "Tito's Handmade Vodka")
]

demand_stats = []

for brand, description in top_products_list:
    # Filter for this product
    product_sales = jan_sales[
        (jan_sales['Brand'] == brand) &
        (jan_sales['Description'] == description)
    ]

    # Daily aggregation
    daily_demand = product_sales.groupby('SalesDate')['SalesQuantity'].sum()

    # Calculate statistics
    avg_daily_demand = daily_demand.mean()
    std_daily_demand = daily_demand.std()
    max_daily_demand = daily_demand.max()
    min_daily_demand = daily_demand.min()

    demand_stats.append({
        'Brand': brand,
        'Product': description,
        'Avg_Daily_Demand': round(avg_daily_demand, 2),
        'Std_Daily_Demand': round(std_daily_demand, 2),
        'Max_Daily_Demand': int(max_daily_demand),
        'Min_Daily_Demand': int(min_daily_demand)
    })

demand_df = pd.DataFrame(demand_stats)

print(" DAILY DEMAND STATISTICS (Based on January 2016):\n")
display(demand_df)

print("\n Daily demand calculated from historical data!")
print("="*70)


 REORDER POINT ANALYSIS - Calculate Daily Demand

 DAILY DEMAND STATISTICS (Based on January 2016):



Brand                  Product  Avg_Daily_Demand  Std_Daily_Demand  \
0   4261   Capt Morgan Spiced Rum            578.61            325.75   
1   3545          Ketel One Vodka            359.90            212.32   
2   1233  Jack Daniels No 7 Black            273.39            133.02   
3   8068         Absolut 80 Proof            311.65            149.65   
4   3405    Tito's Handmade Vodka            268.65            169.15   

   Max_Daily_Demand  Min_Daily_Demand  
0              1227               172  
1               844               110  
2               566                94  
3               589               130  
4               672                72


 Daily demand calculated from historical data!


# Calculate Lead Time from Purchase Data
Analyzing purchase records to find how long it takes suppliers to deliver products.

In [80]:
print("\n REORDER POINT ANALYSIS - Calculate Lead Time\n")
print("="*70)

# Use purchases data
purchases_df = cleaned_data['purchases'].copy()

# Calculate lead time (days between PO Date and Receiving Date)
purchases_df['LeadTime_Days'] = (
    purchases_df['ReceivingDate'] - purchases_df['PODate']
).dt.days

# Remove negative or zero lead times (data errors)
purchases_df = purchases_df[purchases_df['LeadTime_Days'] > 0]

# Calculate lead time for top products
lead_time_stats = []

for brand, description in top_products_list:
    # Filter for this product
    product_purchases = purchases_df[purchases_df['Brand'] == brand]

    if len(product_purchases) > 0:
        avg_lead_time = product_purchases['LeadTime_Days'].mean()
        max_lead_time = product_purchases['LeadTime_Days'].max()
        min_lead_time = product_purchases['LeadTime_Days'].min()
    else:
        # Default values if no purchase data
        avg_lead_time = 7  # Assume 1 week default
        max_lead_time = 14
        min_lead_time = 3

    lead_time_stats.append({
        'Brand': brand,
        'Product': description,
        'Avg_Lead_Time_Days': round(avg_lead_time, 1),
        'Max_Lead_Time_Days': int(max_lead_time),
        'Min_Lead_Time_Days': int(min_lead_time)
    })

lead_time_df = pd.DataFrame(lead_time_stats)

print(" LEAD TIME STATISTICS:\n")
display(lead_time_df)

print("\n Lead time calculated from purchase history!")
print("="*70)


 REORDER POINT ANALYSIS - Calculate Lead Time

 LEAD TIME STATISTICS:



Brand                  Product  Avg_Lead_Time_Days  Max_Lead_Time_Days  \
0   4261   Capt Morgan Spiced Rum                 7.3                  14   
1   3545          Ketel One Vodka                 7.4                  14   
2   1233  Jack Daniels No 7 Black                 7.4                  14   
3   8068         Absolut 80 Proof                 7.4                  14   
4   3405    Tito's Handmade Vodka                 7.6                  14   

   Min_Lead_Time_Days  
0                   3  
1                   3  
2                   3  
3                   3  
4                   3


 Lead time calculated from purchase history!


# Calculate Safety Stock
Determining buffer inventory based on demand variability and desired service level.

In [81]:
print("\n REORDER POINT ANALYSIS - Calculate Safety Stock\n")
print("="*70)

# Service level factor (Z-score)
# 95% service level = 1.65, 99% service level = 2.33
SERVICE_LEVEL = 0.95
Z_SCORE = 1.65  # 95% service level

print(f"Using {SERVICE_LEVEL*100:.0f}% service level (Z-score: {Z_SCORE})")
print("\n" + "-"*70)

# Merge demand and lead time data
rop_analysis = demand_df.merge(
    lead_time_df[['Brand', 'Avg_Lead_Time_Days', 'Max_Lead_Time_Days']],
    on='Brand'
)

# Calculate safety stock
# Formula: Z × Std_Demand × √Lead_Time
rop_analysis['Safety_Stock'] = (
    Z_SCORE *
    rop_analysis['Std_Daily_Demand'] *
    np.sqrt(rop_analysis['Avg_Lead_Time_Days'])
).round(0).astype(int)

print("\nSAFETY STOCK CALCULATION:\n")
display(rop_analysis[['Product', 'Std_Daily_Demand', 'Avg_Lead_Time_Days', 'Safety_Stock']])

print("\nSafety stock calculated!")
print("="*70)


 REORDER POINT ANALYSIS - Calculate Safety Stock

Using 95% service level (Z-score: 1.65)

----------------------------------------------------------------------

SAFETY STOCK CALCULATION:



Product  Std_Daily_Demand  Avg_Lead_Time_Days  Safety_Stock
0   Capt Morgan Spiced Rum            325.75                 7.3          1452
1          Ketel One Vodka            212.32                 7.4           953
2  Jack Daniels No 7 Black            133.02                 7.4           597
3         Absolut 80 Proof            149.65                 7.4           672
4    Tito's Handmade Vodka            169.15                 7.6           769


Safety stock calculated!


# Calculate Reorder Point
Computing the exact inventory level at which to place new orders.

In [82]:
print("\n REORDER POINT ANALYSIS - Calculate Reorder Point\n")
print("="*70)

# Calculate Reorder Point
# ROP = (Average Daily Demand × Lead Time) + Safety Stock
rop_analysis['Reorder_Point'] = (
    (rop_analysis['Avg_Daily_Demand'] * rop_analysis['Avg_Lead_Time_Days']) +
    rop_analysis['Safety_Stock']
).round(0).astype(int)

# Calculate for max lead time scenario (worst case)
rop_analysis['Reorder_Point_WorstCase'] = (
    (rop_analysis['Avg_Daily_Demand'] * rop_analysis['Max_Lead_Time_Days']) +
    rop_analysis['Safety_Stock']
).round(0).astype(int)

print(" REORDER POINT ANALYSIS RESULTS:\n")
display(rop_analysis[[
    'Product',
    'Avg_Daily_Demand',
    'Avg_Lead_Time_Days',
    'Safety_Stock',
    'Reorder_Point',
    'Reorder_Point_WorstCase'
]])

print("\n Reorder points calculated!")
print("="*70)


 REORDER POINT ANALYSIS - Calculate Reorder Point

 REORDER POINT ANALYSIS RESULTS:



Product  Avg_Daily_Demand  Avg_Lead_Time_Days  \
0   Capt Morgan Spiced Rum            578.61                 7.3   
1          Ketel One Vodka            359.90                 7.4   
2  Jack Daniels No 7 Black            273.39                 7.4   
3         Absolut 80 Proof            311.65                 7.4   
4    Tito's Handmade Vodka            268.65                 7.6   

   Safety_Stock  Reorder_Point  Reorder_Point_WorstCase  
0          1452           5676                     9553  
1           953           3616                     5992  
2           597           2620                     4424  
3           672           2978                     5035  
4           769           2811                     4530


 Reorder points calculated!


# Visualize Reorder Point Components
Creating a stacked bar chart showing how reorder points are composed.

In [83]:
print("\n REORDER POINT ANALYSIS - Visualize Components\n")
print("="*70)

# Calculate base demand during lead time
rop_analysis['Base_Demand_During_Lead_Time'] = (
    rop_analysis['Avg_Daily_Demand'] * rop_analysis['Avg_Lead_Time_Days']
).round(0).astype(int)

# Create stacked bar chart
fig = go.Figure()

# Base demand during lead time
fig.add_trace(go.Bar(
    name='Demand During Lead Time',
    x=rop_analysis['Product'],
    y=rop_analysis['Base_Demand_During_Lead_Time'],
    marker_color='steelblue'
))

# Safety stock
fig.add_trace(go.Bar(
    name='Safety Stock (Buffer)',
    x=rop_analysis['Product'],
    y=rop_analysis['Safety_Stock'],
    marker_color='orange'
))

fig.update_layout(
    title=' Reorder Point Components by Product',
    xaxis_title='Product',
    yaxis_title='Units',
    barmode='stack',
    height=500,
    showlegend=True,
    hovermode='x unified'
)

fig.show()

print(" Visualization created!")
print("="*70)


 REORDER POINT ANALYSIS - Visualize Components



 Visualization created!


# Create Inventory Management Guidelines
Generating actionable recommendations for each product.

In [84]:
print("\nREORDER POINT ANALYSIS - Management Guidelines\n")
print("="*70)

print("\n INVENTORY MANAGEMENT RECOMMENDATIONS:\n")

for idx, row in rop_analysis.iterrows():
    product = row['Product']
    avg_demand = row['Avg_Daily_Demand']
    lead_time = row['Avg_Lead_Time_Days']
    safety_stock = row['Safety_Stock']
    rop = row['Reorder_Point']
    rop_worst = row['Reorder_Point_WorstCase']

    print(f"\n{'='*70}")
    print(f" {product}")
    print(f"{'='*70}")
    print(f"Average Daily Demand: {avg_demand:.0f} units/day")
    print(f"Average Lead Time: {lead_time:.0f} days")
    print(f"Safety Stock: {safety_stock} units")
    print(f"\n REORDER POINT: {rop} units")
    print(f"    Worst Case ROP: {rop_worst} units (max lead time)")
    print(f"\n MANAGEMENT ACTIONS:")
    print(f"   1. When inventory drops to {rop} units → Place order immediately")
    print(f"   2. Maintain minimum {safety_stock} units as safety buffer")
    print(f"   3. Order quantity should cover {lead_time:.0f} days of demand")
    print(f"   4. Expected consumption during lead time: {int(avg_demand * lead_time)} units")

print(f"\n{'='*70}")


REORDER POINT ANALYSIS - Management Guidelines


 INVENTORY MANAGEMENT RECOMMENDATIONS:


 Capt Morgan Spiced Rum
Average Daily Demand: 579 units/day
Average Lead Time: 7 days
Safety Stock: 1452 units

 REORDER POINT: 5676 units
    Worst Case ROP: 9553 units (max lead time)

 MANAGEMENT ACTIONS:
   1. When inventory drops to 5676 units → Place order immediately
   2. Maintain minimum 1452 units as safety buffer
   3. Order quantity should cover 7 days of demand
   4. Expected consumption during lead time: 4223 units

 Ketel One Vodka
Average Daily Demand: 360 units/day
Average Lead Time: 7 days
Safety Stock: 953 units

 REORDER POINT: 3616 units
    Worst Case ROP: 5992 units (max lead time)

 MANAGEMENT ACTIONS:
   1. When inventory drops to 3616 units → Place order immediately
   2. Maintain minimum 953 units as safety buffer
   3. Order quantity should cover 7 days of demand
   4. Expected consumption during lead time: 2663 units

 Jack Daniels No 7 Black
Average Daily Demand: 273

# Save Reorder Point Analysis
Exporting the analysis to CSV for business use.

In [85]:
print("\n REORDER POINT ANALYSIS - Save Results\n")
print("="*70)

# Save full analysis
rop_output_path = '/content/Reorder_Point_Analysis.csv'
rop_analysis.to_csv(rop_output_path, index=False)

print(f"Reorder Point Analysis saved to: {rop_output_path}")

# Create summary for quick reference
rop_summary = rop_analysis[[
    'Product',
    'Avg_Daily_Demand',
    'Avg_Lead_Time_Days',
    'Reorder_Point',
    'Safety_Stock'
]].copy()

rop_summary_path = '/content/Reorder_Point_Summary.csv'
rop_summary.to_csv(rop_summary_path, index=False)

print(f" Quick Reference Summary saved to: {rop_summary_path}")

print("\n Files saved successfully!")
print("="*70)


 REORDER POINT ANALYSIS - Save Results

Reorder Point Analysis saved to: /content/Reorder_Point_Analysis.csv
 Quick Reference Summary saved to: /content/Reorder_Point_Summary.csv

 Files saved successfully!


# Compare Current vs. Recommended Inventory Levels
Checking if current inventory (from end inventory data) is above or below reorder points.

In [86]:
print("\n REORDER POINT ANALYSIS - Current Inventory Check\n")
print("="*70)

# Get end inventory data
end_inv = cleaned_data['end_inventory'].copy()

# Check current inventory for top products
current_inventory = []

for brand, description in top_products_list:
    # Filter for this product across all stores
    product_inv = end_inv[end_inv['Brand'] == brand]

    if len(product_inv) > 0:
        total_on_hand = product_inv['onHand'].sum()
        stores_stocking = len(product_inv)
        avg_per_store = total_on_hand / stores_stocking if stores_stocking > 0 else 0
    else:
        total_on_hand = 0
        stores_stocking = 0
        avg_per_store = 0

    current_inventory.append({
        'Product': description,
        'Total_OnHand': int(total_on_hand),
        'Stores_Stocking': stores_stocking,
        'Avg_Per_Store': round(avg_per_store, 1)
    })

current_inv_df = pd.DataFrame(current_inventory)

# Merge with reorder point analysis
inventory_status = rop_analysis[['Product', 'Reorder_Point', 'Safety_Stock']].merge(
    current_inv_df, on='Product'
)

# Calculate status
inventory_status['Status'] = inventory_status.apply(
    lambda row: ' Above ROP' if row['Total_OnHand'] > row['Reorder_Point']
    else ' Below ROP - ORDER NOW!' if row['Total_OnHand'] < row['Reorder_Point']
    else ' At ROP - Monitor Closely',
    axis=1
)

inventory_status['Units_Above_Below_ROP'] = (
    inventory_status['Total_OnHand'] - inventory_status['Reorder_Point']
)

print(" CURRENT INVENTORY STATUS vs REORDER POINTS:\n")
display(inventory_status)

print("\n ACTION ITEMS:")
below_rop = inventory_status[inventory_status['Units_Above_Below_ROP'] < 0]
if len(below_rop) > 0:
    print(f"\n URGENT: {len(below_rop)} product(s) below reorder point!")
    for _, row in below_rop.iterrows():
        shortage = abs(row['Units_Above_Below_ROP'])
        print(f"   • {row['Product']}: {shortage} units below ROP - Order immediately!")
else:
    print("\n All products are at or above reorder points!")

print("="*70)


 REORDER POINT ANALYSIS - Current Inventory Check

 CURRENT INVENTORY STATUS vs REORDER POINTS:



Product  Reorder_Point  Safety_Stock  Total_OnHand  \
0   Capt Morgan Spiced Rum           5676          1452         16769   
1          Ketel One Vodka           3616           953         16770   
2  Jack Daniels No 7 Black           2620           597         15047   
3         Absolut 80 Proof           2978           672         15608   
4    Tito's Handmade Vodka           2811           769         12268   

   Stores_Stocking  Avg_Per_Store      Status  Units_Above_Below_ROP  
0               79          212.3   Above ROP                  11093  
1               79          212.3   Above ROP                  13154  
2               79          190.5   Above ROP                  12427  
3               79          197.6   Above ROP                  12630  
4               79          155.3   Above ROP                   9457


 ACTION ITEMS:

 All products are at or above reorder points!


# **ECONOMIC ORDER QUANTITY (EOQ) ANALYSIS**

## **What is EOQ?**

EOQ (Economic Order Quantity) is the optimal order quantity that minimizes total inventory costs:
- **Ordering Costs**: Cost to place and receive an order
- **Holding Costs**: Cost to store inventory (warehouse, insurance, etc.)

**Formula:** `EOQ = √(2 × Annual Demand × Ordering Cost / Holding Cost per Unit)`

**Goal:** Find the perfect balance between ordering too frequently (high ordering costs) vs. ordering too much (high holding costs).

# Define Cost Parameters

In [87]:
print("\EOQ ANALYSIS - Define Cost Parameters\n")
print("="*70)

# COST ASSUMPTIONS (Industry Standard for Wine & Spirits)
# These would typically come from accounting department

# Ordering costs (per order)
ORDERING_COST = 150  # $ per purchase order (admin, processing, delivery fees)

# Holding costs (annual % of product value)
HOLDING_COST_PERCENTAGE = 0.25  # 25% of product value per year
# This includes: warehousing, insurance, spoilage, capital cost

print(f" COST PARAMETERS:")
print(f"   Ordering Cost: ${ORDERING_COST} per order")
print(f"   Holding Cost: {HOLDING_COST_PERCENTAGE*100}% of product value per year")

print("\Cost parameters defined!")
print("="*70)

\EOQ ANALYSIS - Define Cost Parameters

 COST PARAMETERS:
   Ordering Cost: $150 per order
   Holding Cost: 25.0% of product value per year
\Cost parameters defined!


# Calculate Annual Demand

In [88]:
print("\n EOQ ANALYSIS - Calculate Annual Demand\n")
print("="*70)

# Use January data (most representative month)
sales_df = cleaned_data['sales'].copy()
jan_sales = sales_df[sales_df['SalesDate'].dt.month == 1]

# Calculate annual demand for top 5 products
top_products_list = [
    (4261, 'Capt Morgan Spiced Rum'),
    (3545, 'Ketel One Vodka'),
    (1233, 'Jack Daniels No 7 Black'),
    (8068, 'Absolut 80 Proof'),
    (3405, "Tito's Handmade Vodka")
]

eoq_data = []

for brand, description in top_products_list:
    # Filter for this product
    product_sales = jan_sales[
        (jan_sales['Brand'] == brand) &
        (jan_sales['Description'] == description)
    ]

    # Calculate annual demand (January × 12)
    # Note: Using January as baseline since it's more representative
    monthly_demand = product_sales['SalesQuantity'].sum()
    annual_demand = monthly_demand * 12  # Extrapolate to full year

    # Get average price
    avg_price = product_sales['SalesPrice'].mean()

    eoq_data.append({
        'Brand': brand,
        'Product': description,
        'Monthly_Demand': int(monthly_demand),
        'Annual_Demand': int(annual_demand),
        'Avg_Unit_Price': round(avg_price, 2)
    })

eoq_df = pd.DataFrame(eoq_data)

print("ANNUAL DEMAND PROJECTIONS:\n")
display(eoq_df)

print("\Annual demand calculated!")
print("="*70)


 EOQ ANALYSIS - Calculate Annual Demand

ANNUAL DEMAND PROJECTIONS:



Brand                  Product  Monthly_Demand  Annual_Demand  \
0   4261   Capt Morgan Spiced Rum           17937         215244   
1   3545          Ketel One Vodka           11157         133884   
2   1233  Jack Daniels No 7 Black            8475         101700   
3   8068         Absolut 80 Proof            9661         115932   
4   3405    Tito's Handmade Vodka            8328          99936   

   Avg_Unit_Price  
0           21.99  
1           30.19  
2           35.99  
3           25.88  
4           29.99

\Annual demand calculated!


# Calculate EOQ

In [89]:
print("\EOQ ANALYSIS - Calculate Economic Order Quantity\n")
print("="*70)

# Calculate holding cost per unit per year
eoq_df['Annual_Holding_Cost_Per_Unit'] = (
    eoq_df['Avg_Unit_Price'] * HOLDING_COST_PERCENTAGE
).round(2)

# Calculate EOQ using the formula
# EOQ = √(2 × D × S / H)
# Where: D = Annual Demand, S = Ordering Cost, H = Holding Cost per unit

eoq_df['EOQ'] = np.sqrt(
    (2 * eoq_df['Annual_Demand'] * ORDERING_COST) /
    eoq_df['Annual_Holding_Cost_Per_Unit']
).round(0).astype(int)

# Calculate number of orders per year
eoq_df['Orders_Per_Year'] = (
    eoq_df['Annual_Demand'] / eoq_df['EOQ']
).round(1)

# Calculate total annual costs at EOQ
eoq_df['Total_Annual_Ordering_Cost'] = (
    eoq_df['Orders_Per_Year'] * ORDERING_COST
).round(2)

eoq_df['Total_Annual_Holding_Cost'] = (
    (eoq_df['EOQ'] / 2) * eoq_df['Annual_Holding_Cost_Per_Unit']
).round(2)

eoq_df['Total_Annual_Inventory_Cost'] = (
    eoq_df['Total_Annual_Ordering_Cost'] + eoq_df['Total_Annual_Holding_Cost']
).round(2)

print(" EOQ ANALYSIS RESULTS:\n")
display(eoq_df[[
    'Product',
    'Annual_Demand',
    'Avg_Unit_Price',
    'EOQ',
    'Orders_Per_Year',
    'Total_Annual_Inventory_Cost'
]])

print("\EOQ calculated for all products!")
print("="*70)

\EOQ ANALYSIS - Calculate Economic Order Quantity

 EOQ ANALYSIS RESULTS:



Product  Annual_Demand  Avg_Unit_Price   EOQ  \
0   Capt Morgan Spiced Rum         215244           21.99  3426   
1          Ketel One Vodka         133884           30.19  2306   
2  Jack Daniels No 7 Black         101700           35.99  1841   
3         Absolut 80 Proof         115932           25.88  2319   
4    Tito's Handmade Vodka          99936           29.99  1999   

   Orders_Per_Year  Total_Annual_Inventory_Cost  
0             62.8                     18841.50  
1             58.1                     17420.15  
2             55.2                     16564.50  
3             50.0                     15001.96  
4             50.0                     14996.25

\EOQ calculated for all products!


### **Understanding EOQ Results**

The EOQ tells us:
- **Optimal Order Size**: How many units to order each time
- **Order Frequency**: How often to place orders per year
- **Cost Minimization**: Balancing ordering costs vs. holding costs

**Key Principle:** At EOQ, ordering costs = holding costs (optimal balance)

# Visualize EOQ Components

In [90]:
print("\nEOQ ANALYSIS - Visualize Cost Breakdown\n")
print("="*70)

# Create cost breakdown visualization
fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=('EOQ by Product', 'Annual Cost Breakdown'),
    specs=[[{'type':'bar'}, {'type':'bar'}]]
)

# EOQ quantities
fig.add_trace(
    go.Bar(
        x=eoq_df['Product'],
        y=eoq_df['EOQ'],
        name='EOQ (units)',
        marker_color='steelblue',
        text=eoq_df['EOQ'],
        textposition='auto'
    ),
    row=1, col=1
)

# Cost breakdown (stacked)
fig.add_trace(
    go.Bar(
        x=eoq_df['Product'],
        y=eoq_df['Total_Annual_Ordering_Cost'],
        name='Ordering Costs',
        marker_color='coral'
    ),
    row=1, col=2
)

fig.add_trace(
    go.Bar(
        x=eoq_df['Product'],
        y=eoq_df['Total_Annual_Holding_Cost'],
        name='Holding Costs',
        marker_color='lightblue'
    ),
    row=1, col=2
)

fig.update_layout(
    height=500,
    title_text="Economic Order Quantity Analysis",
    showlegend=True
)

fig.update_xaxes(title_text="Product", row=1, col=1)
fig.update_xaxes(title_text="Product", row=1, col=2)
fig.update_yaxes(title_text="Units", row=1, col=1)
fig.update_yaxes(title_text="Annual Cost ($)", row=1, col=2)

fig.update_layout(barmode='stack', hovermode='x unified')

fig.show()

print("Visualizations created!")
print("="*70)


EOQ ANALYSIS - Visualize Cost Breakdown



Visualizations created!


# Cost Sensitivity Analysis

In [91]:
print("\nEOQ ANALYSIS - Cost Sensitivity Analysis\n")
print("="*70)

# Compare EOQ vs Current Ordering Pattern
print(" COST COMPARISON: EOQ vs Alternative Order Sizes\n")

# Example: Calculate costs for Capt Morgan at different order quantities
product = eoq_df.iloc[0]  # Capt Morgan
product_name = product['Product']
annual_demand = product['Annual_Demand']
holding_cost = product['Annual_Holding_Cost_Per_Unit']
eoq_optimal = product['EOQ']

# Test different order quantities
order_quantities = [500, 1000, int(eoq_optimal), 2000, 3000, 5000]
sensitivity_results = []

for qty in order_quantities:
    orders_per_year = annual_demand / qty
    ordering_cost = orders_per_year * ORDERING_COST
    holding_cost_total = (qty / 2) * holding_cost
    total_cost = ordering_cost + holding_cost_total

    sensitivity_results.append({
        'Order_Quantity': qty,
        'Orders_Per_Year': round(orders_per_year, 1),
        'Ordering_Cost': round(ordering_cost, 2),
        'Holding_Cost': round(holding_cost_total, 2),
        'Total_Cost': round(total_cost, 2)
    })

sensitivity_df = pd.DataFrame(sensitivity_results)

print(f" Cost Sensitivity for: {product_name}\n")
display(sensitivity_df)

# Highlight optimal
optimal_idx = sensitivity_df['Total_Cost'].idxmin()
print(f"\n OPTIMAL ORDER QUANTITY: {sensitivity_df.loc[optimal_idx, 'Order_Quantity']} units")
print(f"   Minimum Total Cost: ${sensitivity_df.loc[optimal_idx, 'Total_Cost']:,.2f}")

print("="*70)


EOQ ANALYSIS - Cost Sensitivity Analysis

 COST COMPARISON: EOQ vs Alternative Order Sizes

 Cost Sensitivity for: Capt Morgan Spiced Rum



Order_Quantity  Orders_Per_Year  Ordering_Cost  Holding_Cost  Total_Cost
0             500            430.5       64573.20        1375.0    65948.20
1            1000            215.2       32286.60        2750.0    35036.60
2            3426             62.8        9423.99        9421.5    18845.49
3            2000            107.6       16143.30        5500.0    21643.30
4            3000             71.7       10762.20        8250.0    19012.20
5            5000             43.0        6457.32       13750.0    20207.32


 OPTIMAL ORDER QUANTITY: 3426 units
   Minimum Total Cost: $18,845.49


# EOQ Business Recommendations

In [92]:
print("\n EOQ ANALYSIS - Business Recommendations\n")
print("="*70)

print("\n EOQ-BASED ORDERING RECOMMENDATIONS:\n")

for idx, row in eoq_df.iterrows():
    product = row['Product']
    eoq = row['EOQ']
    orders_per_year = row['Orders_Per_Year']
    annual_cost = row['Total_Annual_Inventory_Cost']
    avg_price = row['Avg_Unit_Price']

    # Calculate order value
    order_value = eoq * avg_price

    # Days between orders
    days_between_orders = 365 / orders_per_year

    print(f"\n{'='*70}")
    print(f" {product}")
    print(f"{'='*70}")
    print(f" Optimal Order Quantity (EOQ): {eoq:,} units")
    print(f" Order Frequency: {orders_per_year:.1f} times per year ({days_between_orders:.0f} days between orders)")
    print(f" Order Value: ${order_value:,.2f}")
    print(f" Total Annual Inventory Cost: ${annual_cost:,.2f}")
    print(f"\n ACTION PLAN:")
    print(f"   1. Place orders of {eoq:,} units each time")
    print(f"   2. Order approximately every {days_between_orders:.0f} days")
    print(f"   3. Budget ${order_value:,.2f} per order")
    print(f"   4. Annual inventory cost: ${annual_cost:,.2f}")

print(f"\n{'='*70}")
print(" EOQ ANALYSIS COMPLETE!")
print(f"{'='*70}")


 EOQ ANALYSIS - Business Recommendations


 EOQ-BASED ORDERING RECOMMENDATIONS:


 Capt Morgan Spiced Rum
 Optimal Order Quantity (EOQ): 3,426 units
 Order Frequency: 62.8 times per year (6 days between orders)
 Order Value: $75,337.74
 Total Annual Inventory Cost: $18,841.50

 ACTION PLAN:
   1. Place orders of 3,426 units each time
   2. Order approximately every 6 days
   3. Budget $75,337.74 per order
   4. Annual inventory cost: $18,841.50

 Ketel One Vodka
 Optimal Order Quantity (EOQ): 2,306 units
 Order Frequency: 58.1 times per year (6 days between orders)
 Order Value: $69,618.14
 Total Annual Inventory Cost: $17,420.15

 ACTION PLAN:
   1. Place orders of 2,306 units each time
   2. Order approximately every 6 days
   3. Budget $69,618.14 per order
   4. Annual inventory cost: $17,420.15

 Jack Daniels No 7 Black
 Optimal Order Quantity (EOQ): 1,841 units
 Order Frequency: 55.2 times per year (7 days between orders)
 Order Value: $66,257.59
 Total Annual Inventory Cost: $16

# Save EOQ Results

In [93]:
print("\n EOQ ANALYSIS - Save Results\n")
print("="*70)

# Save full EOQ analysis
eoq_output_path = '/content/EOQ_Analysis.csv'
eoq_df.to_csv(eoq_output_path, index=False)

print(f" EOQ Analysis saved to: {eoq_output_path}")

# Create quick reference summary
eoq_summary = eoq_df[[
    'Product',
    'Annual_Demand',
    'EOQ',
    'Orders_Per_Year',
    'Total_Annual_Inventory_Cost'
]].copy()

eoq_summary_path = '/content/EOQ_Summary.csv'
eoq_summary.to_csv(eoq_summary_path, index=False)

print(f"EOQ Summary saved to: {eoq_summary_path}")

print("\nFiles saved successfully!")
print("="*70)


 EOQ ANALYSIS - Save Results

 EOQ Analysis saved to: /content/EOQ_Analysis.csv
EOQ Summary saved to: /content/EOQ_Summary.csv

Files saved successfully!


# LEAD TIME ANALYSIS
Deep-dive into supplier efficiency, delivery consistency, and procurement optimization opportunities.

# Vendor Performance Metrics
Analyze supplier delivery speeds and reliability

# Prepare Lead Time Data
Calculate lead times with robust data validation

In [94]:
print("\nLEAD TIME ANALYSIS - Prepare Lead Time Data\n")
print("="*70)

purchases_df = cleaned_data['purchases'].copy()

# Ensure datetime format
purchases_df['PODate'] = pd.to_datetime(purchases_df['PODate'])
purchases_df['ReceivingDate'] = pd.to_datetime(purchases_df['ReceivingDate'])

# Calculate lead time
purchases_df['LeadTime_Days'] = (
    purchases_df['ReceivingDate'] - purchases_df['PODate']
).dt.days

# Remove invalid lead times (negative or zero)
valid_purchases = purchases_df[purchases_df['LeadTime_Days'] > 0]

print(f" Valid purchase records: {len(valid_purchases):,}")
print(f" Lead time range: {valid_purchases['LeadTime_Days'].min()} to {valid_purchases['LeadTime_Days'].max()} days")
print(f" Average lead time: {valid_purchases['LeadTime_Days'].mean():.1f} days")
print("="*70)


LEAD TIME ANALYSIS - Prepare Lead Time Data

 Valid purchase records: 2,372,474
 Lead time range: 3 to 14 days
 Average lead time: 7.6 days


# Vendor Performance Metrics
Calculate average lead times and consistency scores by supplier

In [95]:
print("\n LEAD TIME ANALYSIS - Vendor-Level Statistics\n")
print("="*70)

# Group by vendor (using VendorName if available, fallback to VendorNumber)
groupby_cols = ['VendorNumber']
if 'VendorName' in valid_purchases.columns:
    groupby_cols.append('VendorName')

vendor_stats = valid_purchases.groupby(groupby_cols).agg(
    Avg_Lead_Time=('LeadTime_Days', 'mean'),
    Median_Lead_Time=('LeadTime_Days', 'median'),
    Std_Lead_Time=('LeadTime_Days', 'std'),
    Min_Lead_Time=('LeadTime_Days', 'min'),
    Max_Lead_Time=('LeadTime_Days', 'max'),
    Total_POs=('LeadTime_Days', 'count'),
    Total_Spend=('Dollars', 'sum'),
    Total_Quantity=('Quantity', 'sum')
).reset_index()

# Try to get vendor names from purchase data
if 'VendorName' in valid_purchases.columns:
    vendor_names = valid_purchases.groupby('VendorNumber')['VendorName'].first().to_dict()
    vendor_stats['Vendor_Name'] = vendor_stats['VendorNumber'].map(vendor_names)
else:
    # Create from InvoicePurchases if available
    try:
        invoice_df = cleaned_data['invoice_purchases']
        if 'VendorName' in invoice_df.columns:
            vendor_names = invoice_df.groupby('VendorNumber')['VendorName'].first().to_dict()
            vendor_stats['Vendor_Name'] = vendor_stats['VendorNumber'].map(vendor_names)
    except:
        vendor_stats['Vendor_Name'] = 'Unknown'

# Clean up nulls and round
vendor_stats['Std_Lead_Time'] = vendor_stats['Std_Lead_Time'].fillna(0).round(2)
vendor_stats['Avg_Lead_Time'] = vendor_stats['Avg_Lead_Time'].round(2)
vendor_stats['CV'] = (vendor_stats['Std_Lead_Time'] / vendor_stats['Avg_Lead_Time']).round(2)

# FIX: Apply minimum PO threshold BEFORE classification
MIN_PO_THRESHOLD = 10
vendor_stats = vendor_stats[vendor_stats['Total_POs'] >= MIN_PO_THRESHOLD]  # Filter here!

print(f"Filtered to {len(vendor_stats)} vendors with ≥{MIN_PO_THRESHOLD} POs")

print(f"\n TOP 10 FASTEST VENDORS:")
display(vendor_stats.nsmallest(10, 'Avg_Lead_Time')[['VendorNumber', 'Vendor_Name', 'Avg_Lead_Time', 'Median_Lead_Time', 'Total_POs', 'CV']])

print(f"\n TOP 10 SLOWEST VENDORS:")
display(vendor_stats.nlargest(10, 'Avg_Lead_Time')[['VendorNumber', 'Vendor_Name', 'Avg_Lead_Time', 'Max_Lead_Time', 'Total_POs', 'Total_Spend']])
print("="*70)


 LEAD TIME ANALYSIS - Vendor-Level Statistics

Filtered to 120 vendors with ≥10 POs

 TOP 10 FASTEST VENDORS:


VendorNumber                  Vendor_Name  Avg_Lead_Time  \
41           3951  HIGHLAND WINE MERCHANTS LLC           5.32   
51           5083             LOYAL DOG WINERY           5.95   
25           1703         ALISA CARR BEVERAGES           6.81   
23           1650                  Circa Wines           6.95   
83           9206        PHILLIPS PRODUCTS CO.           7.01   
72           8150      SEA HAGG DISTILLERY LLC           7.02   
59           6355                  NICHE W & S           7.07   
57           6215            MOONLIGHT MEADERY           7.08   
123         98450            Serralles Usa LLC           7.12   
79           8892     TRINCHERO FAMILY ESTATES           7.13   

     Median_Lead_Time  Total_POs    CV  
41                6.0         28  0.41  
51                5.5         20  0.41  
25                7.0         63  0.40  
23                7.0        233  0.28  
83                7.0       4981  0.30  
72                7.0       1183  0.29  
59                7.0        788  0.33  
57                7.0        681  0.35  
123               7.0       1509  0.30  
79                7.0      33271  0.32


 TOP 10 SLOWEST VENDORS:


VendorNumber                    Vendor_Name  Avg_Lead_Time  \
0               2  IRA GOLDMAN AND WILLIAMS, LLP           9.62   
122         90059           BLACK COVE BEVERAGES           9.32   
89           9751             VINEDREA WINES LLC           8.82   
120         90057        WALPOLE MTN VIEW WINERY           8.53   
124         99166          STARK BREWING COMPANY           8.49   
82           9165     ULTRA BEVERAGE COMPANY LLP           8.41   
116         90051          FULCHINO VINEYARD INC           8.38   
58           6280                       UNCORKED           8.31   
126        173357            TAMWORTH DISTILLING           8.31   
75           8663           STAR INDUSTRIES INC.           8.24   

     Max_Lead_Time  Total_POs  Total_Spend  
0               11         13      5630.88  
122             13         44     14465.06  
89              12         33      4657.60  
120             12         74      9292.31  
124             12         41     25961.04  
82              14      84034  13210613.93  
116             12         74     11147.77  
58              12         16      2966.31  
126             12        153     41036.44  
75              13         17      2452.29

# Intelligent Risk Classification
Classify vendors using median-based thresholds (data-driven)

In [96]:
print("\n LEAD TIME ANALYSIS - Vendor Risk Classification\n")
print("="*70)

# Use median thresholds for data-driven classification
AVG_THRESHOLD = vendor_stats['Avg_Lead_Time'].median()
STD_THRESHOLD = vendor_stats['Std_Lead_Time'].median()

print(f" Classification Thresholds (Median-based):")
print(f"   Average Lead Time Threshold: {AVG_THRESHOLD:.1f} days")
print(f"   Variability Threshold: {STD_THRESHOLD:.1f} days")

def classify_vendor(row):
    """Classify based on both speed and consistency"""
    if row['Avg_Lead_Time'] <= AVG_THRESHOLD and row['Std_Lead_Time'] <= STD_THRESHOLD:
        return ' Premium (Fast & Reliable)'
    elif row['Avg_Lead_Time'] > AVG_THRESHOLD and row['Std_Lead_Time'] > STD_THRESHOLD:
        return ' High Risk (Slow & Unpredictable)'
    elif row['Avg_Lead_Time'] <= AVG_THRESHOLD and row['Std_Lead_Time'] > STD_THRESHOLD:
        return ' Fast but Variable'
    else:
        return ' Slow but Steady'

vendor_stats['Vendor_Risk'] = vendor_stats.apply(classify_vendor, axis=1)

# Now safe to display with Vendor_Risk
display_cols = ['VendorNumber', 'Vendor_Name', 'Avg_Lead_Time', 'Total_POs', 'Vendor_Risk']
print(f"\nSample classified vendors:")
display(vendor_stats[display_cols].head(10))

# Summary table
risk_summary = vendor_stats['Vendor_Risk'].value_counts().reset_index()
risk_summary.columns = ['Risk_Category', 'Vendor_Count']
risk_summary['Percentage'] = (risk_summary['Vendor_Count'] / risk_summary['Vendor_Count'].sum() * 100).round(1)

print(f"\n VENDOR RISK DISTRIBUTION:\n")
display(risk_summary)
print("="*70)


 LEAD TIME ANALYSIS - Vendor Risk Classification

 Classification Thresholds (Median-based):
   Average Lead Time Threshold: 7.7 days
   Variability Threshold: 2.2 days

Sample classified vendors:


VendorNumber                    Vendor_Name  Avg_Lead_Time  Total_POs  \
0              2  IRA GOLDMAN AND WILLIAMS, LLP           9.62         13   
2             60        ADAMBA IMPORTS INTL INC           7.61        626   
3            105             ALTAMAR BRANDS LLC           7.58         57   
5            287           APPOLO VINEYARDS LLC           7.44         18   
6            388     ATLANTIC IMPORTING COMPANY           8.10        266   
7            480                BACARDI USA INC           7.70      91846   
8            516            BANFI PRODUCTS CORP           7.47      23510   
9            653           STATE WINE & SPIRITS           7.75      11406   
10           660     SAZERAC NORTH AMERICA INC.           7.51      54331   
11          1003            BRONCO WINE COMPANY           7.84         49   

                          Vendor_Risk  
0                     Slow but Steady  
2           Premium (Fast & Reliable)  
3                   Fast but Variable  
5           Premium (Fast & Reliable)  
6                     Slow but Steady  
7    High Risk (Slow & Unpredictable)  
8           Premium (Fast & Reliable)  
9    High Risk (Slow & Unpredictable)  
10                  Fast but Variable  
11                    Slow but Steady


 VENDOR RISK DISTRIBUTION:



Risk_Category  Vendor_Count  Percentage
0                    Slow but Steady            35        29.2
1                  Fast but Variable            34        28.3
2          Premium (Fast & Reliable)            26        21.7
3   High Risk (Slow & Unpredictable)            25        20.8

# Advanced Visualizations
4-panel comprehensive dashboard

In [97]:
print("\n LEAD TIME ANALYSIS - Visualization Dashboard\n")
print("="*70)
print("Generating 4-panel visualization...\n")

fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=('Vendor Risk Scatter (Size = Spend)',
                   'Lead Time Distribution',
                   'Financial Impact by Risk Tier',
                   'Top 15 Vendors Lead Time Spread'),
    specs=[[{'type': 'scatter'}, {'type': 'histogram'}],
           [{'type': 'bar'}, {'type': 'box'}]]
)

# 1. Scatter plot: Speed vs Reliability
colors = {'Premium (Fast & Reliable)': '#2ecc71',
          'Slow but Steady': '#3498db',
          'Fast but Variable': '#f1c40f',
          'High Risk (Slow & Unpredictable)': '#e74c3c'}

for risk_class in vendor_stats['Vendor_Risk'].unique():
    mask = vendor_stats['Vendor_Risk'] == risk_class
    subset = vendor_stats[mask]

    fig.add_trace(
        go.Scatter(
            x=subset['Avg_Lead_Time'],
            y=subset['Std_Lead_Time'],
            mode='markers',
            name=risk_class,
            marker=dict(
                size=np.log(subset['Total_Spend'] + 1) * 3,  # Size by spend
                color=colors.get(risk_class, 'gray'),
                opacity=0.7,
                line=dict(width=1, color='black')
            ),
            text=subset['VendorNumber'],
            hovertemplate='<b>Vendor:</b> %{text}<br>' +
                         '<b>Avg Lead:</b> %{x:.1f} days<br>' +
                         '<b>Std Dev:</b> %{y:.1f} days<br>' +
                         '<b>Spend:</b> $%{marker.size:.0f}<extra></extra>'
        ),
        row=1, col=1
    )

# 2. Histogram: Lead time distribution
fig.add_trace(
    go.Histogram(
        x=valid_purchases['LeadTime_Days'],
        nbinsx=30,
        marker_color='steelblue',
        opacity=0.7,
        name='Lead Time Dist'
    ),
    row=1, col=2
)

# 3. Financial Impact by Risk Tier
financial_impact = vendor_stats.groupby('Vendor_Risk').agg({
    'Total_Spend': 'sum',
    'Total_POs': 'sum'
}).reset_index()

fig.add_trace(
    go.Bar(
        x=financial_impact['Vendor_Risk'],
        y=financial_impact['Total_Spend'],
        marker_color=[colors.get(x, 'gray') for x in financial_impact['Vendor_Risk']],
        name='Total Spend',
        text=financial_impact['Total_Spend'].apply(lambda x: f'${x:,.0f}'),
        textposition='auto'
    ),
    row=2, col=1
)

# 4. Box plots for top 15 vendors by spend
top_15_vendors = vendor_stats.nlargest(15, 'Total_Spend')['VendorNumber'].tolist()

for i, vendor in enumerate(top_15_vendors[:5]):  # Show top 5 for clarity
    vendor_data = valid_purchases[valid_purchases['VendorNumber'] == vendor]['LeadTime_Days']
    vendor_spend = vendor_stats[vendor_stats['VendorNumber'] == vendor]['Total_Spend'].iloc[0]

    fig.add_trace(
        go.Box(
            y=vendor_data,
            name=f"Vendor {vendor}",
            boxpoints='outliers',
            hovertemplate=f"<b>Vendor {vendor}</b><br>Spend: ${vendor_spend:,.0f}<br>Days: %{{y}}<extra></extra>"
        ),
        row=2, col=2
    )

fig.update_layout(
    height=900,
    title_text="Lead Time Analysis Dashboard - Vendor Performance Overview",
    showlegend=True,
    hovermode='closest'
)

fig.update_xaxes(title_text="Average Lead Time (Days)", row=1, col=1)
fig.update_yaxes(title_text="Variability (Std Dev)", row=1, col=1)
fig.update_xaxes(title_text="Lead Time (Days)", row=1, col=2)
fig.update_yaxes(title_text="Frequency", row=1, col=2)
fig.update_xaxes(title_text="Vendor Risk Category", row=2, col=1)
fig.update_yaxes(title_text="Total Spend ($)", row=2, col=1)
fig.update_yaxes(title_text="Lead Time (Days)", row=2, col=2)

fig.show()
print("Dashboard generated!")
print("="*70)


 LEAD TIME ANALYSIS - Visualization Dashboard

Generating 4-panel visualization...



Dashboard generated!


# A-Class Product Supplier Review
Critical integration with ABC Analysis

In [98]:
print("\n LEAD TIME ANALYSIS - A-Class Product Supplier Review + Risk Analysis\n")
print("="*70)

# Top brands from ABC Analysis
top_brands = [4261, 3545, 1233, 8068, 3405]
brand_names = {
    4261: 'Capt Morgan Spiced Rum',
    3545: 'Ketel One Vodka',
    1233: 'Jack Daniels No 7 Black',
    8068: 'Absolut 80 Proof',
    3405: "Tito's Handmade Vodka"
}

aclass_purchases = valid_purchases[valid_purchases['Brand'].isin(top_brands)]

if len(aclass_purchases) > 0:
    aclass_vendor_stats = aclass_purchases.groupby(
        ['Brand', 'VendorNumber']
    ).agg(
        Avg_Lead_Time=('LeadTime_Days', 'mean'),
        Std_Lead_Time=('LeadTime_Days', 'std'),
        Total_POs=('LeadTime_Days', 'count'),
        Avg_Cost=('Dollars', 'mean')
    ).reset_index()

    aclass_vendor_stats['Std_Lead_Time'] = aclass_vendor_stats['Std_Lead_Time'].fillna(0).round(2)
    aclass_vendor_stats['Avg_Lead_Time'] = aclass_vendor_stats['Avg_Lead_Time'].round(2)

    # Add product names
    aclass_vendor_stats['Product'] = aclass_vendor_stats['Brand'].map(brand_names)

    # Add risk classification from previous step
    aclass_vendor_stats = aclass_vendor_stats.merge(
        vendor_stats[['VendorNumber', 'Vendor_Risk', 'Vendor_Name']],
        on='VendorNumber',
        how='left'
    )

    print(" A-CLASS PRODUCT SUPPLIER PERFORMANCE:\n")
    display_cols = ['Product', 'VendorNumber', 'Vendor_Name', 'Avg_Lead_Time', 'Std_Lead_Time', 'Vendor_Risk', 'Total_POs']
    display(aclass_vendor_stats[display_cols].sort_values(['Product', 'Avg_Lead_Time']))

    # Critical risk alert
    high_risk_acl = aclass_vendor_stats[aclass_vendor_stats['Vendor_Risk'].str.contains('High Risk', na=False)]
    if len(high_risk_acl) > 0:
        print("\n CRITICAL ALERT: High-risk vendors supplying A-Class products!")
        display(high_risk_acl[['Product', 'VendorNumber', 'Vendor_Name', 'Avg_Lead_Time', 'Vendor_Risk']])

    # 5.1: Find Premium alternatives
    print("\n FINDING PREMIUM VENDOR ALTERNATIVES FOR A-CLASS PRODUCTS\n")
    premium_vendors = vendor_stats[vendor_stats['Vendor_Risk'].str.contains('Premium', na=False)]

    for brand_id, brand_name in brand_names.items():
        current_info = aclass_vendor_stats[aclass_vendor_stats['Brand'] == brand_id]
        if len(current_info) == 0: continue

        current_vendor = current_info['VendorNumber'].iloc[0]
        current_risk = current_info['Vendor_Risk'].iloc[0]

        brand_purchases = valid_purchases[valid_purchases['Brand'] == brand_id]
        brand_vendors = brand_purchases.groupby('VendorNumber').agg({
            'LeadTime_Days': 'mean',
            'Dollars': 'sum'
        }).reset_index()

        brand_vendors = brand_vendors.merge(
            vendor_stats[['VendorNumber', 'Vendor_Risk']],
            on='VendorNumber'
        )

        premium_alternatives = brand_vendors[brand_vendors['Vendor_Risk'].str.contains('Premium', na=False)]

        if len(premium_alternatives) > 0 and 'Premium' not in str(current_risk):
            print(f"  {brand_name}:")
            print(f"   Current: Vendor {current_vendor} ({current_risk})")
            print(f"   Alternative Premium vendors available:")
            for _, alt in premium_alternatives.iterrows():
                print(f"      → Vendor {alt['VendorNumber']}: {alt['LeadTime_Days']:.1f} days, ${alt['Dollars']:,.0f} volume")
        elif 'Premium' not in str(current_risk):
            print(f" {brand_name}: NO PREMIUM ALTERNATIVES FOUND - Dual-source immediately!")

    # 5.2: Concentration risk
    print("\n VENDOR CONCENTRATION RISK ANALYSIS\n")
    vendor_aclass_count = aclass_vendor_stats['VendorNumber'].value_counts()
    multi_product_vendors = vendor_aclass_count[vendor_aclass_count > 1]

    if len(multi_product_vendors) > 0:
        print(" Vendors supplying MULTIPLE A-Class products (Concentration Risk):")
        for vendor, count in multi_product_vendors.items():
            products = aclass_vendor_stats[aclass_vendor_stats['VendorNumber'] == vendor]['Product'].tolist()
            print(f"   • Vendor {vendor}: Supplies {count} products ({', '.join(products)})")
            print(f"     Risk: If this vendor fails, you lose {count}/5 top products\n")
else:
    print(" No purchase records found for A-Class products in this period")

print("="*70)


 LEAD TIME ANALYSIS - A-Class Product Supplier Review + Risk Analysis

 A-CLASS PRODUCT SUPPLIER PERFORMANCE:



Product  VendorNumber               Vendor_Name  \
4         Absolut 80 Proof         17035         PERNOD RICARD USA   
3   Capt Morgan Spiced Rum          3960  DIAGEO NORTH AMERICA INC   
0  Jack Daniels No 7 Black          1128         BROWN-FORMAN CORP   
2          Ketel One Vodka          3960  DIAGEO NORTH AMERICA INC   
1    Tito's Handmade Vodka          4425     MARTIGNETTI COMPANIES   

   Avg_Lead_Time  Std_Lead_Time         Vendor_Risk  Total_POs  
4           7.39           2.19   Fast but Variable       7359  
3           7.34           2.21   Fast but Variable       6774  
0           7.44           2.22   Fast but Variable       6584  
2           7.36           2.20   Fast but Variable       6326  
1           7.56           2.16     Slow but Steady       6506


 FINDING PREMIUM VENDOR ALTERNATIVES FOR A-CLASS PRODUCTS

 Capt Morgan Spiced Rum: NO PREMIUM ALTERNATIVES FOUND - Dual-source immediately!
 Ketel One Vodka: NO PREMIUM ALTERNATIVES FOUND - Dual-source immediately!
 Jack Daniels No 7 Black: NO PREMIUM ALTERNATIVES FOUND - Dual-source immediately!
 Absolut 80 Proof: NO PREMIUM ALTERNATIVES FOUND - Dual-source immediately!
 Tito's Handmade Vodka: NO PREMIUM ALTERNATIVES FOUND - Dual-source immediately!

 VENDOR CONCENTRATION RISK ANALYSIS

 Vendors supplying MULTIPLE A-Class products (Concentration Risk):
   • Vendor 3960: Supplies 2 products (Ketel One Vodka, Capt Morgan Spiced Rum)
     Risk: If this vendor fails, you lose 2/5 top products



# Financial Impact Analysis
Quantify procurement risk by dollar exposure

In [99]:
print("\n LEAD TIME ANALYSIS - Financial Impact by Risk Tier\n")
print("="*70)

financial_summary = vendor_stats.groupby('Vendor_Risk').agg({
    'Total_Spend': ['sum', 'mean', 'count'],
    'Total_POs': 'sum',
    'Avg_Lead_Time': 'mean',
    'CV': 'mean'
}).round(2)

financial_summary.columns = ['Total_Spend', 'Avg_Spend_Per_Vendor', 'Vendor_Count', 'Total_POs', 'Avg_Lead_Days', 'Avg_CV']
financial_summary['Spend_Percentage'] = (financial_summary['Total_Spend'] / financial_summary['Total_Spend'].sum() * 100).round(1)

# Reorder for display hierarchy
tier_order = [' Premium (Fast & Reliable)', ' Slow but Steady', ' Fast but Variable', ' High Risk (Slow & Unpredictable)']
financial_summary = financial_summary.reindex([x for x in tier_order if x in financial_summary.index])

print(" FINANCIAL EXPOSURE BY SUPPLIER TIER:\n")
display(financial_summary)

# Calculate risk exposure
total_spend = financial_summary['Total_Spend'].sum()
risky_spend = financial_summary.loc[' High Risk (Slow & Unpredictable)', 'Total_Spend'] if ' High Risk (Slow & Unpredictable)' in financial_summary.index else 0
variable_spend = financial_summary.loc[' Fast but Variable', 'Total_Spend'] if ' Fast but Variable' in financial_summary.index else 0

HIGH_SPEND_THRESHOLD = vendor_stats['Total_Spend'].quantile(0.90)  # Top 10% spenders

high_spend_slow = vendor_stats[
    (vendor_stats['Total_Spend'] > HIGH_SPEND_THRESHOLD) &
    (vendor_stats['Avg_Lead_Time'] > AVG_THRESHOLD)
]

if len(high_spend_slow) > 0:
    print(f"\n CRITICAL: HIGH-SPEND SLOW VENDORS (Top 10% spenders slower than median)")
    print(f"   These vendors cost you speed AND money:\n")
    display(high_spend_slow[['VendorNumber', 'Vendor_Name', 'Total_Spend', 'Total_POs',
                            'Avg_Lead_Time', 'Vendor_Risk']].sort_values('Total_Spend', ascending=False))

    total_at_risk = high_spend_slow['Total_Spend'].sum()
    print(f"\n Total spend with slow high-volume vendors: ${total_at_risk:,.2f}")
    print(f"    Action: Renegotiate SLAs with penalty clauses for late delivery")

print(f"\n KEY METRICS:")
print(f"   • Total Procurement Exposure: ${total_spend:,.2f}")
print(f"   • High-Risk Vendor Exposure: ${risky_spend:,.2f} ({risky_spend/total_spend*100:.1f}%)")
print(f"   • Variable Vendor Exposure: ${variable_spend:,.2f} ({variable_spend/total_spend*100:.1f}%)")
print(f"   • Reliable Vendor Coverage: {(total_spend-risky_spend-variable_spend)/total_spend*100:.1f}%")

print("="*70)


 LEAD TIME ANALYSIS - Financial Impact by Risk Tier

 FINANCIAL EXPOSURE BY SUPPLIER TIER:



Total_Spend  Avg_Spend_Per_Vendor  \
Vendor_Risk                                                            
Premium (Fast & Reliable)         5.058038e+07            1945399.20   
Slow but Steady                   8.290529e+07            2368722.63   
Fast but Variable                 1.649460e+08            4851351.65   
High Risk (Slow & Unpredictable)  2.346717e+07             938686.92   

                                  Vendor_Count  Total_POs  Avg_Lead_Days  \
Vendor_Risk                                                                
Premium (Fast & Reliable)                   26     442482           7.38   
Slow but Steady                             35     672199           8.08   
Fast but Variable                           34    1125973           7.33   
High Risk (Slow & Unpredictable)            25     131803           7.93   

                                  Avg_CV  Spend_Percentage  
Vendor_Risk                                                 
Premium (Fast & Reliable)           0.28              15.7  
Slow but Steady                     0.25              25.8  
Fast but Variable                   0.32              51.2  
High Risk (Slow & Unpredictable)    0.29               7.3


 CRITICAL: HIGH-SPEND SLOW VENDORS (Top 10% spenders slower than median)
   These vendors cost you speed AND money:



VendorNumber                 Vendor_Name  Total_Spend  Total_POs  \
44          4425       MARTIGNETTI COMPANIES  27861690.02     176781   
7            480             BACARDI USA INC  17624378.72      91846   
16          1392    CONSTELLATION BRANDS INC  15573917.90     185574   
82          9165  ULTRA BEVERAGE COMPANY LLP  13210613.93      84034   
85          9552              M S WALKER INC  10935817.30     112792   

    Avg_Lead_Time                        Vendor_Risk  
44           7.79                    Slow but Steady  
7            7.70   High Risk (Slow & Unpredictable)  
16           7.74                    Slow but Steady  
82           8.41                    Slow but Steady  
85           7.91                    Slow but Steady


 Total spend with slow high-volume vendors: $85,206,417.87
    Action: Renegotiate SLAs with penalty clauses for late delivery

 KEY METRICS:
   • Total Procurement Exposure: $321,898,800.26
   • High-Risk Vendor Exposure: $23,467,173.12 (7.3%)
   • Variable Vendor Exposure: $164,945,956.03 (51.2%)
   • Reliable Vendor Coverage: 41.5%


# Strategic Recommendations
Actionable procurement strategy

In [100]:
print("\n LEAD TIME ANALYSIS - Strategic Recommendations\n")
print("="*70)

# Identify specific problematic vendors
high_spend_slow = vendor_stats[
    (vendor_stats['Total_Spend'] > vendor_stats['Total_Spend'].quantile(0.75)) &
    (vendor_stats['Avg_Lead_Time'] > AVG_THRESHOLD)
]

high_variability_critical = vendor_stats[
    (vendor_stats['CV'] > 0.5) &
    (vendor_stats['Total_POs'] > 20)
]

print(" STRATEGIC INSIGHTS:\n")

print("1 SUPPLIER PORTFOLIO HEALTH:")
print(f"   • {len(vendor_stats[vendor_stats['Vendor_Risk'].str.contains('Premium')])} Premium vendors ({len(vendor_stats[vendor_stats['Vendor_Risk'].str.contains('Premium')])/len(vendor_stats)*100:.0f}%)")
print(f"   • {len(vendor_stats[vendor_stats['Vendor_Risk'].str.contains('High Risk')])} High-risk vendors")
print(f"   • Average lead time: {vendor_stats['Avg_Lead_Time'].mean():.1f} days")

if len(high_spend_slow) > 0:
    print(f"\n2 HIGH-PRIORITY NEGOTIATIONS:")
    print(f"   • {len(high_spend_slow)} high-spend vendors are slower than median")
    print(f"   • Combined spend: ${high_spend_slow['Total_Spend'].sum():,.2f}")
    print("   • Action: Renegotiate SLAs or find alternative sources")

if len(high_variability_critical) > 0:
    print(f"\n3️ CONSISTENCY ISSUES:")
    print(f"   • {len(high_variability_critical)} vendors show high variability (>50% CV) with significant order volume")
    print("   • Action: Implement vendor-managed inventory or increase safety stock")

print(f"\n4️ A-CLASS PRODUCT STRATEGY:")
if 'aclass_vendor_stats' in locals() and len(aclass_vendor_stats) > 0:
    # Check actual risk categories
    premium_count = len(aclass_vendor_stats[aclass_vendor_stats['Vendor_Risk'].str.contains('Premium', na=False)])
    variable_count = len(aclass_vendor_stats[aclass_vendor_stats['Vendor_Risk'].str.contains('Variable', na=False)])
    high_risk_count = len(aclass_vendor_stats[aclass_vendor_stats['Vendor_Risk'].str.contains('High Risk', na=False)])
    slow_steady_count = len(aclass_vendor_stats[aclass_vendor_stats['Vendor_Risk'].str.contains('Slow but Steady', na=False)])

    print(f"   •  Premium Vendors: {premium_count}/5 products")
    print(f"   •  Fast but Variable: {variable_count}/5 products ")
    print(f"   •  Slow but Steady: {slow_steady_count}/5 products")
    print(f"   •  High Risk: {high_risk_count}/5 products")

    if premium_count == 0:
        print(f"\n    CRITICAL GAP: No A-Class products use Premium vendors!")
        print(f"      All top revenue products are with variable or slow suppliers.")
        print(f"      Action: Immediate supplier development/negotiation required.")
    elif variable_count > 0:
        print(f"\n    WARNING: {variable_count} A-Class products use variable suppliers")
        print(f"      Risk of stockouts during demand spikes.")
else:
    print("   •  Review purchase data linkage for A-Class products")
    print("   •  Review purchase data linkage for A-Class products")

print(f"\n5️ IMMEDIATE ACTIONS:")
print(f"   • Consolidate {vendor_stats.nlargest(3, 'Total_POs')['Total_POs'].sum()} orders from top 3 vendors to negotiate volume discounts")
print(f"   • Set safety stock multiplier to 1.5x for 'Fast but Variable' vendors")
print(f"   • Negotiate penalty clauses with vendors having CV > 0.8")
print("="*70)


 LEAD TIME ANALYSIS - Strategic Recommendations

 STRATEGIC INSIGHTS:

1 SUPPLIER PORTFOLIO HEALTH:
   • 26 Premium vendors (22%)
   • 25 High-risk vendors
   • Average lead time: 7.7 days

2 HIGH-PRIORITY NEGOTIATIONS:
   • 7 high-spend vendors are slower than median
   • Combined spend: $94,833,640.94
   • Action: Renegotiate SLAs or find alternative sources

4️ A-CLASS PRODUCT STRATEGY:
   •  Premium Vendors: 0/5 products
   •  Fast but Variable: 4/5 products 
   •  Slow but Steady: 1/5 products
   •  High Risk: 0/5 products

    CRITICAL GAP: No A-Class products use Premium vendors!
      All top revenue products are with variable or slow suppliers.
      Action: Immediate supplier development/negotiation required.

5️ IMMEDIATE ACTIONS:
   • Consolidate 618732 orders from top 3 vendors to negotiate volume discounts
   • Set safety stock multiplier to 1.5x for 'Fast but Variable' vendors
   • Negotiate penalty clauses with vendors having CV > 0.8


# Export Results
Save analysis for downstream use

In [101]:
print("\n LEAD TIME ANALYSIS - Save Results\n")
print("="*70)

# Save complete vendor scorecard
vendor_file = '/content/Vendor_Performance_Scorecard.csv'
vendor_stats.to_csv(vendor_file, index=False)
print(f"Vendor Scorecard: {vendor_file}")

# Save A-Class vendor analysis
if 'aclass_vendor_stats' in locals() and len(aclass_vendor_stats) > 0:
    aclass_file = '/content/AClass_Vendor_Analysis.csv'
    aclass_vendor_stats.to_csv(aclass_file, index=False)
    print(f" A-Class Analysis: {aclass_file}")

# Save raw lead time data for audit
raw_file = '/content/LeadTime_Raw_Data.csv'
valid_purchases[['VendorNumber', 'Brand', 'LeadTime_Days', 'Dollars', 'Quantity', 'PODate', 'ReceivingDate']].to_csv(raw_file, index=False)
print(f" Raw Data: {raw_file}")

print("\n Files ready for procurement team review!")
print("="*70)
print("\nLead Time Analysis Finished!")
print("="*70)


 LEAD TIME ANALYSIS - Save Results

Vendor Scorecard: /content/Vendor_Performance_Scorecard.csv
 A-Class Analysis: /content/AClass_Vendor_Analysis.csv
 Raw Data: /content/LeadTime_Raw_Data.csv

 Files ready for procurement team review!

Lead Time Analysis Finished!
